# OVERVIEW

## TITLE : Telangana Growth Analysis

### Objective:
• Explore Stamp Registration, Transportation and Ts-Ipass Datasets.

• Understand their attributes, categories and time period.

• Analyze trends and patterns within each department.

• Identify growth opportunities and areas needing attention.

• Find correlation among these departments and report the overall growth of the state through insights and relevant visuals such as shape maps.


# PYSPARK IMPORTS

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.window import Window
from pyspark.sql import functions as F
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.ml.stat import *
from pyspark.ml.feature import *

# LIBRARIES

In [0]:
import numpy as np
import pandas as pd

# VISUALIZATION LIBRARY

In [0]:
import matplotlib.pyplot as plt
from matplotlib.ticker import FuncFormatter
import plotly.graph_objects as go
import plotly.express as px
import plotly.figure_factory as ff
# import plotly.subplots as sp
# import matplotlib.pyplot as plt
# import plotly.express as px
# import plotly.graph_objects as go
# import plotly.io as pio
# from plotly.offline import *
# init_notebook_mode(connected=True)
# from plotly.graph_objs import *

import warnings
warnings.filterwarnings('ignore')


# SPARK SESSION

In [0]:
# Assuming you have a SparkSession named spark
spark = SparkSession.builder.appName("Telangana").getOrCreate()
spark.conf.set("spark.sql.legacy.allowCreatingManagedTableUsingNonemptyLocation","true")
spark

# EXTRACTION

In [0]:
df1 = spark.read.format("csv").option("header", "true").option("sep", ",").option("inferschema", "true").load("dbfs:/FileStore/shared_uploads/sparshsonawane212468@gmail.com/dim_districts.csv")
df2 = spark.read.format("csv").option("header", "true").option("sep", ",").option("inferschema", "true").load("dbfs:/FileStore/shared_uploads/sparshsonawane212468@gmail.com/dim_date.csv")
df3 = spark.read.format("csv").option("header", "true").option("sep", ",").option("inferschema", "true").load("dbfs:/FileStore/shared_uploads/sparshsonawane212468@gmail.com/fact_stamps.csv")
df4 = spark.read.format("csv").option("header", "true").option("sep", ",").option("inferschema", "true").load("dbfs:/FileStore/shared_uploads/sparshsonawane212468@gmail.com/fact_transport.csv")
df5 = spark.read.format("csv").option("header", "true").option("sep", ",").option("inferschema", "true").load("dbfs:/FileStore/shared_uploads/sparshsonawane212468@gmail.com/fact_TS_iPASS.csv")

# LOAD IN DBFS

In [0]:
# Loop through each DataFrame and save it with its original name
for i in range(1, 6):
    df = locals()[f"df{i}"]
    table_name = f"table_{i}"  # Change this to the desired table name or use the original name
    df.write.format("parquet").mode("overwrite").saveAsTable(table_name)

# SCHEMA

In [0]:
# printschema for each data frame
for i in range(1, 6):
    df = locals()[f"df{i}"]
    print(f"Schema for DataFrame {i}:")
    df.printSchema()
    print("\n")

Schema for DataFrame 1:
root
 |-- dist_code: string (nullable = true)
 |-- district: string (nullable = true)



Schema for DataFrame 2:
root
 |-- month: date (nullable = true)
 |-- Mmm: string (nullable = true)
 |-- quarter: string (nullable = true)
 |-- fiscal_year: integer (nullable = true)



Schema for DataFrame 3:
root
 |-- dist_code: string (nullable = true)
 |-- month: date (nullable = true)
 |-- documents_registered_cnt: integer (nullable = true)
 |-- documents_registered_rev: long (nullable = true)
 |-- estamps_challans_cnt: integer (nullable = true)
 |-- estamps_challans_rev: long (nullable = true)



Schema for DataFrame 4:
root
 |-- dist_code: string (nullable = true)
 |-- month: date (nullable = true)
 |-- fuel_type_petrol: integer (nullable = true)
 |-- fuel_type_diesel: integer (nullable = true)
 |-- fuel_type_electric: integer (nullable = true)
 |-- fuel_type_others: integer (nullable = true)
 |-- vehicleClass_MotorCycle: integer (nullable = true)
 |-- vehicleClass_Mot

# DISPLAY

In [0]:
# display for each data frame
for i in range(1, 6):
    df = locals()[f"df{i}"]
    print(f"Display for DataFrame {i}:")
    display(df)
    print("\n")

Display for DataFrame 1:


dist_code district 19_1 Adilabad 22_2 Bhadradri Kothagudem 21_1 Hanumakonda 16_1 Hyderabad 20_2 Jagtial 21_3 Jangoan 21_7 Jayashankar Bhupalpally 14_2 Jogulamba Gadwal 18_2 Kamareddy 20_1 Karimnagar 22_1 Khammam 19_4 Kumurambheem Asifabad 21_5 Mahabubabad 14_1 Mahabubnagar 19_3 Mancherial 17_1 Medak 15_2 Medchal_Malkajgiri 21_6 Mulugu 14_3 Nagarkurnool 23_1 Nalgonda 14_5 Narayanpet 19_2 Nirmal 18_1 Nizamabad 20_4 Peddapalli 20_3 Rajanna Sircilla 15_1 Rangareddy 17_2 Sangareddy 17_3 Siddipet 23_2 Suryapet 15_3 Vikarabad 14_4 Wanaparthy 21_2 Warangal 23_3 Yadadri Bhuvanagiri



Display for DataFrame 2:


month Mmm quarter fiscal_year 2019-04-01 Apr Q1 2019 2019-05-01 May Q1 2019 2019-06-01 Jun Q1 2019 2019-07-01 Jul Q2 2019 2019-08-01 Aug Q2 2019 2019-09-01 Sep Q2 2019 2019-10-01 Oct Q3 2019 2019-11-01 Nov Q3 2019 2019-12-01 Dec Q3 2019 2020-01-01 Jan Q4 2019 2020-02-01 Feb Q4 2019 2020-03-01 Mar Q4 2019 2020-04-01 Apr Q1 2020 2020-05-01 May Q1 2020 2020-06-01 Jun Q1 2020 2020-07-01 Jul Q2 2020 2020-08-01 Aug Q2 2020 2020-09-01 Sep Q2 2020 2020-10-01 Oct Q3 2020 2020-11-01 Nov Q3 2020 2020-12-01 Dec Q3 2020 2021-01-01 Jan Q4 2020 2021-02-01 Feb Q4 2020 2021-03-01 Mar Q4 2020 2021-04-01 Apr Q1 2021 2021-05-01 May Q1 2021 2021-06-01 Jun Q1 2021 2021-07-01 Jul Q2 2021 2021-08-01 Aug Q2 2021 2021-09-01 Sep Q2 2021 2021-10-01 Oct Q3 2021 2021-11-01 Nov Q3 2021 2021-12-01 Dec Q3 2021 2022-01-01 Jan Q4 2021 2022-02-01 Feb Q4 2021 2022-03-01 Mar Q4 2021 2022-04-01 Apr Q1 2022 2022-05-01 May Q1 2022 2022-06-01 Jun Q1 2022 2022-07-01 Jul Q2 2022 2022-08-01 Aug Q2 2022 2022-09-01 Sep Q2 2022 2022-10-01 Oct Q3 2022 2022-11-01 Nov Q3 2022 2022-12-01 Dec Q3 2022 2023-01-01 Jan Q4 2022 2023-02-01 Feb Q4 2022 2023-03-01 Mar Q4 2022



Display for DataFrame 3:


dist_code month documents_registered_cnt documents_registered_rev estamps_challans_cnt estamps_challans_rev 14_1 2019-04-01 4533 59236363 0 0 17_3 2019-04-01 4151 41508762 0 0 20_3 2019-04-01 2116 23674170 0 0 21_5 2019-04-01 1089 15915285 0 0 23_1 2019-04-01 6133 82593256 0 0 23_3 2019-04-01 7413 113680902 0 0 20_1 2019-04-01 2748 58308650 0 0 20_4 2019-04-01 1384 27467135 0 0 16_1 2019-04-01 5268 724238098 0 0 14_3 2019-04-01 2726 21804047 0 0 15_2 2019-04-01 14140 1080766807 0 0 21_6 2019-04-01 563 5688052 0 0 22_2 2019-04-01 542 12610700 0 0 20_2 2019-04-01 1943 26031616 0 0 14_2 2019-04-01 2074 17019180 0 0 21_2 2019-04-01 947 10639865 0 0 22_1 2019-04-01 4088 89082890 0 0 17_2 2019-04-01 8316 418960714 0 0 23_2 2019-04-01 2692 45800865 0 0 19_4 2019-04-01 585 8302945 0 0 19_3 2019-04-01 1620 24326193 0 0 18_2 2019-04-01 2876 26367902 0 0 19_1 2019-04-01 1043 12672655 0 0 14_5 2019-04-01 2091 13948976 0 0 14_4 2019-04-01 2355 19227636 0 0 18_1 2019-04-01 4562 60415544 0 0 19_2 2019-04-01 1767 18940764 0 0 21_1 2019-04-01 4186 120047007 0 0 15_1 2019-04-01 29436 2026355727 0 0 17_1 2019-04-01 2205 30584778 0 0 21_3 2019-04-01 2372 30706161 0 0 15_3 2019-04-01 2259 26570227 0 0 21_2 2019-05-01 1230 15030867 0 0 18_2 2019-05-01 3352 26907600 0 0 20_2 2019-05-01 2312 29341793 0 0 22_2 2019-05-01 782 12779175 0 0 21_6 2019-05-01 616 6059339 0 0 19_3 2019-05-01 2260 33143566 0 0 22_1 2019-05-01 5095 93397223 0 0 17_1 2019-05-01 2400 68953812 0 0 17_3 2019-05-01 4478 49926112 0 0 23_3 2019-05-01 8787 161615746 0 0 18_1 2019-05-01 5047 71038874 0 0 14_5 2019-05-01 1615 11855661 0 0 21_3 2019-05-01 2968 38073544 0 0 20_1 2019-05-01 3029 60448065 0 0 19_1 2019-05-01 1092 15177385 0 0 19_2 2019-05-01 1788 20714061 0 0 23_1 2019-05-01 6592 90267315 0 0 14_3 2019-05-01 3471 25935850 0 0 17_2 2019-05-01 8494 425344246 0 0 19_4 2019-05-01 414 4902685 0 0 14_2 2019-05-01 2392 21224914 0 0 14_4 2019-05-01 2809 20217773 0 0 15_1 2019-05-01 31310 2027201202 0 0 16_1 2019-05-01 5210 754708131 0 0 14_1 2019-05-01 4301 73344601 0 0 20_4 2019-05-01 1554 27369396 0 0 20_3 2019-05-01 2097 23745502 0 0 21_1 2019-05-01 5395 151385340 0 0 15_3 2019-05-01 2347 26915352 0 0 21_5 2019-05-01 1468 19541233 0 0 15_2 2019-05-01 16036 1231074513 0 0 23_2 2019-05-01 3460 53073454 0 0 14_5 2019-06-01 1701 12770293 0 0 20_1 2019-06-01 3276 63248165 0 0 17_3 2019-06-01 5625 50053613 0 0 16_1 2019-06-01 5015 746210249 0 0 21_1 2019-06-01 4541 141468882 0 0 19_3 2019-06-01 1994 26534317 0 0 20_4 2019-06-01 2053 33732651 0 0 21_2 2019-06-01 1276 14677798 0 0 23_3 2019-06-01 9280 106077226 0 0 15_1 2019-06-01 24084 2089441609 0 0 14_3 2019-06-01 4267 29213266 0 0 21_5 2019-06-01 1392 18292822 0 0 23_2 2019-06-01 3319 46934818 0 0 17_2 2019-06-01 8251 388914751 0 0 19_4 2019-06-01 520 5626095 0 0 19_2 2019-06-01 1860 20888875 0 0 14_4 2019-06-01 2527 17696126 0 0 22_1 2019-06-01 5049 99823253 0 0 14_1 2019-06-01 3565 50331243 0 0 22_2 2019-06-01 705 13006275 0 0 15_2 2019-06-01 11808 942570587 0 0 19_1 2019-06-01 824 11443194 0 0 17_1 2019-06-01 2613 45801812 0 0 21_3 2019-06-01 2766 34975070 0 0 18_1 2019-06-01 5258 66957257 0 0 23_1 2019-06-01 7146 104282218 0 0 20_3 2019-06-01 2388 27212704 0 0 18_2 2019-06-01 3595 34889349 0 0 20_2 2019-06-01 2672 32368172 0 0 21_6 2019-06-01 721 6553495 0 0 15_3 2019-06-01 2072 29390216 0 0 14_2 2019-06-01 1753 24300464 0 0 21_3 2019-07-01 3210 38094533 0 0 15_3 2019-07-01 2635 31158113 0 0 21_6 2019-07-01 1022 9855642 0 0 23_2 2019-07-01 4709 70377544 0 0 15_1 2019-07-01 29063 1762830038 0 0 23_1 2019-07-01 8928 115173858 0 0 18_1 2019-07-01 5749 74149259 0 0 19_1 2019-07-01 1186 17853370 0 0 14_1 2019-07-01 5056 58994710 0 0 17_3 2019-07-01 5575 47714647 0 0 18_2 2019-07-01 3835 32920357 0 0 23_3 2019-07-01 9448 134999011 0 0 21_1 2019-07-01 5892 152570326 0 0 19_2 2019-07-01 2127 22890600 0 0 14_4 2019-07-01 3460 22968808 0 0 14_3 2019-07-01 4185 28345301 0 0 20_4 2019-07-01 2236 34112815 0 0 19_3 2019-07-01 2434 33016334 0 



Display for DataFrame 4:


dist_code month fuel_type_petrol fuel_type_diesel fuel_type_electric fuel_type_others vehicleClass_MotorCycle vehicleClass_MotorCar vehicleClass_AutoRickshaw vehicleClass_Agriculture vehicleClass_others seatCapacity_1_to_3 seatCapacity_4_to_6 seatCapacity_above_6 Brand_new_vehicles Pre-owned_vehicles category_Non-Transport category_Transport 15_1 2019-04-01 17910 3011 76 22 15308 4429 0 4 1278 16110 4182 717 19542 1477 19856 1163 18_2 2019-04-01 3066 306 6 0 2995 142 49 64 128 3156 189 33 3322 56 3203 175 20_3 2019-04-01 1577 215 0 0 1546 79 29 21 117 1683 104 5 1751 41 1648 144 21_3 2019-04-01 1961 281 2 0 1939 72 72 48 113 2082 146 16 2209 35 2075 169 21_7 2019-04-01 1552 309 0 0 1512 76 69 109 95 1696 145 20 1820 41 1701 160 14_1 2019-04-01 4550 660 0 0 4431 264 193 84 238 4714 450 44 5104 106 4802 408 17_3 2019-04-01 3112 496 0 0 3038 233 70 72 195 3276 279 53 3470 138 3353 255 14_3 2019-04-01 2200 496 0 0 2160 110 74 162 190 2483 194 19 2645 51 2440 256 19_2 2019-04-01 1736 263 2 9 1678 121 55 70 86 1806 173 31 1980 30 1879 131 14_2 2019-04-01 2033 173 0 0 2017 67 22 47 53 2111 87 8 2162 44 2134 72 20_4 2019-04-01 2066 350 4 5 1993 146 62 69 155 2181 208 34 2371 54 2222 203 15_3 2019-04-01 3636 877 6 2 3502 341 481 74 123 3666 796 59 4412 109 3928 593 19_3 2019-04-01 2006 367 9 14 1924 178 112 12 170 2081 295 20 2330 66 2128 268 23_1 2019-04-01 4656 744 2 12 4481 330 92 200 311 4947 399 68 5294 120 5035 379 23_2 2019-04-01 3295 676 1 2 3192 202 113 120 347 3606 295 71 3911 63 3526 448 20_2 2019-04-01 2786 440 2 0 2720 135 106 121 146 2951 245 30 3120 108 2986 242 23_3 2019-04-01 2468 470 2 12 2398 198 56 81 219 2679 236 37 2899 53 2690 262 20_1 2019-04-01 3028 579 0 15 2897 278 112 60 275 3195 382 45 3514 108 3262 360 16_1 2019-04-01 24309 2957 284 1540 22081 3749 1518 0 1742 23082 5306 698 27121 1969 25973 3117 15_2 2019-04-01 19273 3634 42 16 17309 3871 0 18 1767 18567 3684 695 21570 1395 21326 1639 17_2 2019-04-01 5291 1115 25 8 4854 842 282 56 405 5220 1072 147 6165 274 5808 631 17_1 2019-04-01 2240 439 2 0 2181 145 144 31 180 2374 273 34 2545 136 2363 318 18_1 2019-04-01 4701 772 2 22 4493 481 188 110 225 4785 646 66 5426 71 5096 401 14_4 2019-04-01 1752 262 0 0 1722 72 58 64 98 1865 131 18 1992 22 1865 149 22_1 2019-04-01 5740 760 4 49 5628 345 228 86 266 5939 535 79 6412 141 6077 476 21_5 2019-04-01 1945 297 1 2 1923 48 85 49 140 2087 144 14 2203 42 2030 215 22_2 2019-04-01 3527 669 2 4 3409 234 231 74 254 3683 467 52 4096 106 3725 477 19_1 2019-04-01 1758 326 0 2 1697 116 77 13 183 1823 184 79 2061 25 1832 254 21_2 2019-04-01 5371 999 3 6 5158 537 190 78 416 5564 725 90 6216 163 5792 587 19_4 2019-04-01 1149 155 0 0 1136 27 53 0 88 1212 76 14 1288 16 1167 137 21_2 2019-05-01 6101 988 7 10 5784 635 150 117 420 6168 765 171 6897 209 6558 548 19_1 2019-05-01 1870 190 0 9 1823 96 71 6 73 1883 159 27 2040 29 1926 143 22_2 2019-05-01 3364 828 2 2 3260 249 245 185 257 3635 487 74 4097 99 3708 488 21_5 2019-05-01 2126 415 0 0 2089 72 76 91 213 2347 151 43 2503 38 2257 284 22_1 2019-05-01 4989 926 0 56 4845 364 250 166 346 5274 626 65 5671 300 5399 572 18_1 2019-05-01 5795 900 4 25 5564 473 234 160 293 5966 673 85 6591 133 6212 512 15_2 2019-05-01 18836 3695 69 47 16642 4123 0 14 1868 17840 3864 929 21106 1541 20919 1728 17_2 2019-05-01 5458 1157 5 2 5050 810 255 46 461 5379 1027 208 6313 309 5949 673 16_1 2019-05-01 24949 3035 83 1755 21847 4028 1705 6 2236 23513 5501 806 27738 2084 26018 3804 14_4 2019-05-01 1587 298 0 0 1555 61 64 71 134 1734 129 22 1831 54 1693 192 15_1 2019-05-01 17962 3280 76 27 15060 4667 0 13 1605 15958 4454 903 19894 1451 19888 1457 23_3 2019-05-01 2404 595 0 16 2321 231 53 144 266 2695 285 35 2942 73 2709 306 17_1 2019-05-01 2134 453 0 0 2076 123 143 86 159 2303 262 22 2509 78 2294 293 20_1 2019-05-01 2846 753 0 14 2698 290 124 105 396 3080 440 93 3510 103 3133 480 19_4 2019-05-01 963 163 2 0 954 33 64 6 71 1023 96 7 1113 15 995 133 23_1 2019-05-01 5141 1103 4 12 5001 367 126 302 464 5654 498 102



Display for DataFrame 5:


dist_code month sector investment in cr number_of_employees 14_1 01-04-2019 Engineering 2.32 15 19_1 01-04-2019 Engineering 0.625 13 20_3 01-04-2019 Wood and Leather 0.2 8 20_3 01-04-2019 Textiles 0.2675 27 21_5 01-04-2019 Electrical and Electronic Products 0.12 5 20_3 01-04-2019 Plastic and Rubber 0.15 4 20_3 01-04-2019 Paper and Printing 0.2 10 19_2 01-04-2019 Cement, Cement & Concrete Products, Fly Ash Bricks 0.03 3 19_2 01-04-2019 Engineering 0.03 0 20_3 01-04-2019 Food Processing 2.02 12 20_3 01-04-2019 Engineering 0.155 6 20_3 01-04-2019 Cement, Cement & Concrete Products, Fly Ash Bricks 0.62 28 23_1 01-04-2019 Plastic and Rubber 1.2916 19 23_1 01-04-2019 Pharmaceuticals and Chemicals 3.0 20 23_1 01-04-2019 Granite and Stone Crushing 0.82 30 23_1 01-04-2019 Food Processing 1.25 20 23_1 01-04-2019 Agro based incl Cold Storages 0.2 10 20_3 01-04-2019 Agro based incl Cold Storages 0.56 24 15_3 01-04-2019 Agro based incl Cold Storages 0.1952 5 15_3 01-04-2019 Food Processing 0.056 5 19_1 01-04-2019 Cement, Cement & Concrete Products, Fly Ash Bricks 19.3702 99 14_3 01-04-2019 Food Processing 0.2346 10 23_2 01-04-2019 Cement, Cement & Concrete Products, Fly Ash Bricks 1.95 25 23_2 01-04-2019 Granite and Stone Crushing 6.0758 60 23_3 01-04-2019 Food Processing 6.1433 50 23_3 01-04-2019 Engineering 2.7 20 20_4 01-04-2019 Engineering 0.08 3 20_4 01-04-2019 Agro based incl Cold Storages 1.014 8 15_2 01-04-2019 Wood and Leather 1.5304 7 15_2 01-04-2019 Real Estate,Industrial Parks and IT Buildings 531.0 70 15_2 01-04-2019 R&D 93.0 50 15_2 01-04-2019 Plastic and Rubber 5.5373 75 15_2 01-04-2019 Pharmaceuticals and Chemicals 9.05 503 15_3 01-04-2019 Plastic and Rubber 0.105 6 15_2 01-04-2019 Paper and Printing 6.1237 462 15_2 01-04-2019 Food Processing 0.4225 265 15_2 01-04-2019 Fertlizers Organic and Inorganic,Pesticides,Insecticides, and Other Related 0.05 5 15_2 01-04-2019 Engineering 36.6737 1159 15_2 01-04-2019 Electrical and Electronic Products 14.95 39 15_2 01-04-2019 Cement, Cement & Concrete Products, Fly Ash Bricks 0.64 4 21_3 01-04-2019 Engineering 0.05 3 18_2 01-04-2019 Food Processing 8.9646 73 14_2 01-04-2019 Agro based incl Cold Storages 1.6982 9 23_2 01-04-2019 Textiles 0.8 6 15_2 01-04-2019 Granite and Stone Crushing 0.0 5 23_3 01-04-2019 Pharmaceuticals and Chemicals 0.0 75 15_3 01-04-2019 Wood and Leather 0.145 4 19_3 01-04-2019 Beverages 0.06 3 15_1 01-04-2019 Plastic and Rubber 3.59 32 15_1 01-04-2019 Real Estate,Industrial Parks and IT Buildings 291.7016 14048 19_4 01-04-2019 Agro based incl Cold Storages 0.05 5 19_4 01-04-2019 Food Processing 1.2124 23 22_1 01-04-2019 Agro based incl Cold Storages 0.57 17 22_1 01-04-2019 Cement, Cement & Concrete Products, Fly Ash Bricks 3.0 25 22_1 01-04-2019 Food Processing 0.2 4 22_1 01-04-2019 Granite and Stone Crushing 4.46 32 22_1 01-04-2019 Paper and Printing 0.4 12 20_1 01-04-2019 Agro based incl Cold Storages 1.475 53 20_1 01-04-2019 Beverages 0.17 4 20_1 01-04-2019 Cement, Cement & Concrete Products, Fly Ash Bricks 2.24 26 20_1 01-04-2019 Engineering 0.07 4 20_1 01-04-2019 Food Processing 0.6645 20 20_1 01-04-2019 Granite and Stone Crushing 4.7 45 20_1 01-04-2019 Textiles 0.3 6 17_1 01-04-2019 Agro based incl Cold Storages 59.5 800 17_1 01-04-2019 Engineering 1.369 10 17_1 01-04-2019 Solar and Other Renewable Energy 318.25 20 15_1 01-04-2019 Pharmaceuticals and Chemicals 0.9975 7 15_1 01-04-2019 Granite and Stone Crushing 2.53 20 15_1 01-04-2019 Food Processing 0.5456 489 15_1 01-04-2019 Engineering 13.4535 149 19_3 01-04-2019 Food Processing 0.05 2 17_2 01-04-2019 Wood and Leather 0.0 12 17_2 01-04-2019 Solar and Other Renewable Energy 27.5 75 17_2 01-04-2019 Plastic and Rubber 33.6 0 17_2 01-04-2019 Pharmaceuticals and Chemicals 9.3749 174 17_2 01-04-2019 Granite and Stone Crushing 4.35 41 17_2 01-04-2019 Food Processing 18.0 250 17_2 01-04-2019 Engineering 3.416 190 17_2 01-04-2019 Cement, Cement & Concrete Products, Fly Ash Bricks 8.3 60 14_4 01-04-2019 Granite an

# TRANSFORM

In [0]:
# Convert 'month' column to datetime format
df5 = df5.withColumn('month', to_date(from_unixtime(unix_timestamp(col('month'), 'dd-MM-yyyy'))))
display(df5)


dist_code month sector investment in cr number_of_employees 14_1 2019-04-01 Engineering 2.32 15 19_1 2019-04-01 Engineering 0.625 13 20_3 2019-04-01 Wood and Leather 0.2 8 20_3 2019-04-01 Textiles 0.2675 27 21_5 2019-04-01 Electrical and Electronic Products 0.12 5 20_3 2019-04-01 Plastic and Rubber 0.15 4 20_3 2019-04-01 Paper and Printing 0.2 10 19_2 2019-04-01 Cement, Cement & Concrete Products, Fly Ash Bricks 0.03 3 19_2 2019-04-01 Engineering 0.03 0 20_3 2019-04-01 Food Processing 2.02 12 20_3 2019-04-01 Engineering 0.155 6 20_3 2019-04-01 Cement, Cement & Concrete Products, Fly Ash Bricks 0.62 28 23_1 2019-04-01 Plastic and Rubber 1.2916 19 23_1 2019-04-01 Pharmaceuticals and Chemicals 3.0 20 23_1 2019-04-01 Granite and Stone Crushing 0.82 30 23_1 2019-04-01 Food Processing 1.25 20 23_1 2019-04-01 Agro based incl Cold Storages 0.2 10 20_3 2019-04-01 Agro based incl Cold Storages 0.56 24 15_3 2019-04-01 Agro based incl Cold Storages 0.1952 5 15_3 2019-04-01 Food Processing 0.056 5 19_1 2019-04-01 Cement, Cement & Concrete Products, Fly Ash Bricks 19.3702 99 14_3 2019-04-01 Food Processing 0.2346 10 23_2 2019-04-01 Cement, Cement & Concrete Products, Fly Ash Bricks 1.95 25 23_2 2019-04-01 Granite and Stone Crushing 6.0758 60 23_3 2019-04-01 Food Processing 6.1433 50 23_3 2019-04-01 Engineering 2.7 20 20_4 2019-04-01 Engineering 0.08 3 20_4 2019-04-01 Agro based incl Cold Storages 1.014 8 15_2 2019-04-01 Wood and Leather 1.5304 7 15_2 2019-04-01 Real Estate,Industrial Parks and IT Buildings 531.0 70 15_2 2019-04-01 R&D 93.0 50 15_2 2019-04-01 Plastic and Rubber 5.5373 75 15_2 2019-04-01 Pharmaceuticals and Chemicals 9.05 503 15_3 2019-04-01 Plastic and Rubber 0.105 6 15_2 2019-04-01 Paper and Printing 6.1237 462 15_2 2019-04-01 Food Processing 0.4225 265 15_2 2019-04-01 Fertlizers Organic and Inorganic,Pesticides,Insecticides, and Other Related 0.05 5 15_2 2019-04-01 Engineering 36.6737 1159 15_2 2019-04-01 Electrical and Electronic Products 14.95 39 15_2 2019-04-01 Cement, Cement & Concrete Products, Fly Ash Bricks 0.64 4 21_3 2019-04-01 Engineering 0.05 3 18_2 2019-04-01 Food Processing 8.9646 73 14_2 2019-04-01 Agro based incl Cold Storages 1.6982 9 23_2 2019-04-01 Textiles 0.8 6 15_2 2019-04-01 Granite and Stone Crushing 0.0 5 23_3 2019-04-01 Pharmaceuticals and Chemicals 0.0 75 15_3 2019-04-01 Wood and Leather 0.145 4 19_3 2019-04-01 Beverages 0.06 3 15_1 2019-04-01 Plastic and Rubber 3.59 32 15_1 2019-04-01 Real Estate,Industrial Parks and IT Buildings 291.7016 14048 19_4 2019-04-01 Agro based incl Cold Storages 0.05 5 19_4 2019-04-01 Food Processing 1.2124 23 22_1 2019-04-01 Agro based incl Cold Storages 0.57 17 22_1 2019-04-01 Cement, Cement & Concrete Products, Fly Ash Bricks 3.0 25 22_1 2019-04-01 Food Processing 0.2 4 22_1 2019-04-01 Granite and Stone Crushing 4.46 32 22_1 2019-04-01 Paper and Printing 0.4 12 20_1 2019-04-01 Agro based incl Cold Storages 1.475 53 20_1 2019-04-01 Beverages 0.17 4 20_1 2019-04-01 Cement, Cement & Concrete Products, Fly Ash Bricks 2.24 26 20_1 2019-04-01 Engineering 0.07 4 20_1 2019-04-01 Food Processing 0.6645 20 20_1 2019-04-01 Granite and Stone Crushing 4.7 45 20_1 2019-04-01 Textiles 0.3 6 17_1 2019-04-01 Agro based incl Cold Storages 59.5 800 17_1 2019-04-01 Engineering 1.369 10 17_1 2019-04-01 Solar and Other Renewable Energy 318.25 20 15_1 2019-04-01 Pharmaceuticals and Chemicals 0.9975 7 15_1 2019-04-01 Granite and Stone Crushing 2.53 20 15_1 2019-04-01 Food Processing 0.5456 489 15_1 2019-04-01 Engineering 13.4535 149 19_3 2019-04-01 Food Processing 0.05 2 17_2 2019-04-01 Wood and Leather 0.0 12 17_2 2019-04-01 Solar and Other Renewable Energy 27.5 75 17_2 2019-04-01 Plastic and Rubber 33.6 0 17_2 2019-04-01 Pharmaceuticals and Chemicals 9.3749 174 17_2 2019-04-01 Granite and Stone Crushing 4.35 41 17_2 2019-04-01 Food Processing 18.0 250 17_2 2019-04-01 Engineering 3.416 190 17_2 2019-04-01 Cement, Cement & Concrete Products, Fly Ash Bricks 8.3 60 14_4 2019-04-01 Granite an

# COLUMNS

In [0]:
# Print column names for each DataFrame
for i in range(1, 6):
    df = locals()[f"df{i}"]
    print(f"Column names for df{i}:")
    print(df.columns)
    print("\n")

Column names for df1:
['dist_code', 'district']


Column names for df2:
['month', 'Mmm', 'quarter', 'fiscal_year']


Column names for df3:
['dist_code', 'month', 'documents_registered_cnt', 'documents_registered_rev', 'estamps_challans_cnt', 'estamps_challans_rev']


Column names for df4:
['dist_code', 'month', 'fuel_type_petrol', 'fuel_type_diesel', 'fuel_type_electric', 'fuel_type_others', 'vehicleClass_MotorCycle', 'vehicleClass_MotorCar', 'vehicleClass_AutoRickshaw', 'vehicleClass_Agriculture', 'vehicleClass_others', 'seatCapacity_1_to_3', 'seatCapacity_4_to_6', 'seatCapacity_above_6', 'Brand_new_vehicles', 'Pre-owned_vehicles', 'category_Non-Transport', 'category_Transport']


Column names for df5:
['dist_code', 'month', 'sector', 'investment in cr', 'number_of_employees']




# ANALYSIS

# <=Stamp Registration=>

## _Stamp Registration Problem Statement 1 =>_

### How does the revenue generated from document registration vary across districts in Telangana? List down the top 5 districts that showed the highest document registration revenue growth between FY 2019 and 2022.

In [0]:
# Filter data based on fiscal years in df2
filtered_df = df3.join(df2, ['month']).filter((col('fiscal_year') >= 2019) & (col('fiscal_year') <= 2022))
display(filtered_df)

month dist_code documents_registered_cnt documents_registered_rev estamps_challans_cnt estamps_challans_rev Mmm quarter fiscal_year 2019-04-01 14_1 4533 59236363 0 0 Apr Q1 2019 2019-04-01 17_3 4151 41508762 0 0 Apr Q1 2019 2019-04-01 20_3 2116 23674170 0 0 Apr Q1 2019 2019-04-01 21_5 1089 15915285 0 0 Apr Q1 2019 2019-04-01 23_1 6133 82593256 0 0 Apr Q1 2019 2019-04-01 23_3 7413 113680902 0 0 Apr Q1 2019 2019-04-01 20_1 2748 58308650 0 0 Apr Q1 2019 2019-04-01 20_4 1384 27467135 0 0 Apr Q1 2019 2019-04-01 16_1 5268 724238098 0 0 Apr Q1 2019 2019-04-01 14_3 2726 21804047 0 0 Apr Q1 2019 2019-04-01 15_2 14140 1080766807 0 0 Apr Q1 2019 2019-04-01 21_6 563 5688052 0 0 Apr Q1 2019 2019-04-01 22_2 542 12610700 0 0 Apr Q1 2019 2019-04-01 20_2 1943 26031616 0 0 Apr Q1 2019 2019-04-01 14_2 2074 17019180 0 0 Apr Q1 2019 2019-04-01 21_2 947 10639865 0 0 Apr Q1 2019 2019-04-01 22_1 4088 89082890 0 0 Apr Q1 2019 2019-04-01 17_2 8316 418960714 0 0 Apr Q1 2019 2019-04-01 23_2 2692 45800865 0 0 Apr Q1 2019 2019-04-01 19_4 585 8302945 0 0 Apr Q1 2019 2019-04-01 19_3 1620 24326193 0 0 Apr Q1 2019 2019-04-01 18_2 2876 26367902 0 0 Apr Q1 2019 2019-04-01 19_1 1043 12672655 0 0 Apr Q1 2019 2019-04-01 14_5 2091 13948976 0 0 Apr Q1 2019 2019-04-01 14_4 2355 19227636 0 0 Apr Q1 2019 2019-04-01 18_1 4562 60415544 0 0 Apr Q1 2019 2019-04-01 19_2 1767 18940764 0 0 Apr Q1 2019 2019-04-01 21_1 4186 120047007 0 0 Apr Q1 2019 2019-04-01 15_1 29436 2026355727 0 0 Apr Q1 2019 2019-04-01 17_1 2205 30584778 0 0 Apr Q1 2019 2019-04-01 21_3 2372 30706161 0 0 Apr Q1 2019 2019-04-01 15_3 2259 26570227 0 0 Apr Q1 2019 2019-05-01 21_2 1230 15030867 0 0 May Q1 2019 2019-05-01 18_2 3352 26907600 0 0 May Q1 2019 2019-05-01 20_2 2312 29341793 0 0 May Q1 2019 2019-05-01 22_2 782 12779175 0 0 May Q1 2019 2019-05-01 21_6 616 6059339 0 0 May Q1 2019 2019-05-01 19_3 2260 33143566 0 0 May Q1 2019 2019-05-01 22_1 5095 93397223 0 0 May Q1 2019 2019-05-01 17_1 2400 68953812 0 0 May Q1 2019 2019-05-01 17_3 4478 49926112 0 0 May Q1 2019 2019-05-01 23_3 8787 161615746 0 0 May Q1 2019 2019-05-01 18_1 5047 71038874 0 0 May Q1 2019 2019-05-01 14_5 1615 11855661 0 0 May Q1 2019 2019-05-01 21_3 2968 38073544 0 0 May Q1 2019 2019-05-01 20_1 3029 60448065 0 0 May Q1 2019 2019-05-01 19_1 1092 15177385 0 0 May Q1 2019 2019-05-01 19_2 1788 20714061 0 0 May Q1 2019 2019-05-01 23_1 6592 90267315 0 0 May Q1 2019 2019-05-01 14_3 3471 25935850 0 0 May Q1 2019 2019-05-01 17_2 8494 425344246 0 0 May Q1 2019 2019-05-01 19_4 414 4902685 0 0 May Q1 2019 2019-05-01 14_2 2392 21224914 0 0 May Q1 2019 2019-05-01 14_4 2809 20217773 0 0 May Q1 2019 2019-05-01 15_1 31310 2027201202 0 0 May Q1 2019 2019-05-01 16_1 5210 754708131 0 0 May Q1 2019 2019-05-01 14_1 4301 73344601 0 0 May Q1 2019 2019-05-01 20_4 1554 27369396 0 0 May Q1 2019 2019-05-01 20_3 2097 23745502 0 0 May Q1 2019 2019-05-01 21_1 5395 151385340 0 0 May Q1 2019 2019-05-01 15_3 2347 26915352 0 0 May Q1 2019 2019-05-01 21_5 1468 19541233 0 0 May Q1 2019 2019-05-01 15_2 16036 1231074513 0 0 May Q1 2019 2019-05-01 23_2 3460 53073454 0 0 May Q1 2019 2019-06-01 14_5 1701 12770293 0 0 Jun Q1 2019 2019-06-01 20_1 3276 63248165 0 0 Jun Q1 2019 2019-06-01 17_3 5625 50053613 0 0 Jun Q1 2019 2019-06-01 16_1 5015 746210249 0 0 Jun Q1 2019 2019-06-01 21_1 4541 141468882 0 0 Jun Q1 2019 2019-06-01 19_3 1994 26534317 0 0 Jun Q1 2019 2019-06-01 20_4 2053 33732651 0 0 Jun Q1 2019 2019-06-01 21_2 1276 14677798 0 0 Jun Q1 2019 2019-06-01 23_3 9280 106077226 0 0 Jun Q1 2019 2019-06-01 15_1 24084 2089441609 0 0 Jun Q1 2019 2019-06-01 14_3 4267 29213266 0 0 Jun Q1 2019 2019-06-01 21_5 1392 18292822 0 0 Jun Q1 2019 2019-06-01 23_2 3319 46934818 0 0 Jun Q1 2019 2019-06-01 17_2 8251 388914751 0 0 Jun Q1 2019 2019-06-01 19_4 520 5626095 0 0 Jun Q1 2019 2019-06-01 19_2 1860 20888875 0 0 Jun Q1 2019 2019-06-01 14_4 2527 17696126 0 0 Jun Q1 2019 2019-06-01 22_1 5049 99823253 0 0 Jun Q1 2019 2019-06-01 14_1 3565 50331243 0 0 Jun Q1 2019 2019-06-01 22_2 705 13006275 0 0 Jun

In [0]:
# Calculate revenue growth for each district
window_spec = Window.partitionBy('dist_code').orderBy('month')
filtered_df = filtered_df.withColumn('prev_month_rev', F.lag('documents_registered_rev').over(window_spec))
filtered_df = filtered_df.withColumn('revenue_growth', ((F.col('documents_registered_rev') - F.col('prev_month_rev')) / F.col('prev_month_rev')) * 100)

# Drop the temporary columns used for calculation
filtered_df = filtered_df.drop('prev_month_rev')

display(filtered_df)

month dist_code documents_registered_cnt documents_registered_rev estamps_challans_cnt estamps_challans_rev Mmm quarter fiscal_year revenue_growth 2019-04-01 14_1 4533 59236363 0 0 Apr Q1 2019 null 2019-05-01 14_1 4301 73344601 0 0 May Q1 2019 23.81685384701961 2019-06-01 14_1 3565 50331243 0 0 Jun Q1 2019 -31.37703073740902 2019-07-01 14_1 5056 58994710 0 0 Jul Q2 2019 17.21290094107153 2019-08-01 14_1 4864 73289753 0 0 Aug Q2 2019 24.23105902207164 2019-09-01 14_1 4281 64062953 0 0 Sep Q2 2019 -12.589481642815741 2019-10-01 14_1 4289 62143167 0 0 Oct Q3 2019 -2.99671793150091 2019-11-01 14_1 4102 60830591 0 0 Nov Q3 2019 -2.1121807325976802 2019-12-01 14_1 4090 88675750 0 0 Dec Q3 2019 45.77492761824392 2020-01-01 14_1 3952 51248313 0 0 Jan Q4 2019 -42.20707126807498 2020-02-01 14_1 4658 62577930 0 0 Feb Q4 2019 22.107297463625777 2020-03-01 14_1 3868 86288684 0 0 Mar Q4 2019 37.88996216397698 2020-04-01 14_1 422 7340232 0 0 Apr Q1 2020 -91.4934013827352 2020-05-01 14_1 2566 25446164 0 0 May Q1 2020 246.66702632832315 2020-06-01 14_1 4493 56964703 0 0 Jun Q1 2020 123.86361653567901 2020-07-01 14_1 3696 47677705 0 0 Jul Q2 2020 -16.30307455478176 2020-08-01 14_1 2895 41587078 0 0 Aug Q2 2020 -12.7745809073654 2020-09-01 14_1 545 5525051 0 0 Sep Q2 2020 -86.71450059559366 2020-10-01 14_1 4 4400 0 0 Oct Q3 2020 -99.92036272606353 2020-11-01 14_1 3 6460 0 0 Nov Q3 2020 46.81818181818182 2020-12-01 14_1 1232 29263859 1403 31343349 Dec Q3 2020 452900.9133126935 2021-01-01 14_1 3954 79370990 4116 79833516 Jan Q4 2020 171.22530217221183 2021-02-01 14_1 3310 71273670 3378 68717372 Feb Q4 2020 -10.20186342642318 2021-03-01 14_1 3573 71235534 3810 75654410 Mar Q4 2020 -0.05350643512534151 2021-04-01 14_1 2784 51136932 2765 50954652 Apr Q1 2021 -28.21429260290237 2021-05-01 14_1 652 18952470 718 18902087 May Q1 2021 -62.93780393395521 2021-06-01 14_1 2509 59654363 2583 81201988 Jun Q1 2021 214.7577228720056 2021-07-01 14_1 2997 103057135 3165 83807604 Jul Q2 2021 72.75707897509524 2021-08-01 14_1 2411 66454883 2548 67040597 Aug Q2 2021 -35.5164656964314 2021-10-01 14_1 2700 79052206 2816 82062938 Oct Q3 2021 18.95620371493243 2021-11-01 14_1 2527 79043084 2610 76616047 Nov Q3 2021 -0.01153920992413545 2021-12-01 14_1 3192 103687749 3287 110176889 Dec Q3 2021 31.178774603480807 2022-01-01 14_1 3788 118531201 3941 129427844 Jan Q4 2021 14.31553114341406 2022-02-01 14_1 2841 102687336 2931 88469993 Feb Q4 2021 -13.366830730079245 2022-03-01 14_1 3699 111740736 3896 110951795 Mar Q4 2021 8.81647177992815 2022-04-01 14_1 3253 105448377 3285 105928140 Apr Q1 2022 -5.63121313251418 2022-05-01 14_1 2983 111506589 3112 116263639 May Q1 2022 5.745192265974848 2022-06-01 14_1 2552 90044509 2598 89618011 Jun Q1 2022 -19.247364835095084 2022-07-01 14_1 2477 85214519 2563 84543841 Jul Q2 2022 -5.364002817762048 2022-08-01 14_1 2619 92104718 2723 96154871 Aug Q2 2022 8.08571013585138 2022-09-01 14_1 2479 78865422 2542 81191094 Sep Q2 2022 -14.37417787870541 2022-10-01 14_1 2331 78745780 2406 74192139 Oct Q3 2022 -0.15170400026516057 2022-11-01 14_1 2867 98486139 2990 100294633 Nov Q3 2022 25.068465891124582 2022-12-01 14_1 2784 85098197 2880 84393869 Dec Q3 2022 -13.59373221037734 2023-01-01 14_1 2326 73940840 2428 75877587 Jan Q4 2022 -13.111155574776747 2023-02-01 14_1 2480 74664336 2532 77460885 Feb Q4 2022 0.9784795520310563 2023-03-01 14_1 2877 91894125 3017 95840642 Mar Q4 2022 23.076330579033076 2019-04-01 14_2 2074 17019180 0 0 Apr Q1 2019 null 2019-05-01 14_2 2392 21224914 0 0 May Q1 2019 24.711731117480397 2019-06-01 14_2 1753 24300464 0 0 Jun Q1 2019 14.490282504796015 2019-07-01 14_2 3068 22574155 0 0 Jul Q2 2019 -7.104016614662173 2019-08-01 14_2 2519 18515918 0 0 Aug Q2 2019 -17.97735950692285 2019-09-01 14_2 1968 12895743 0 0 Sep Q2 2019 -30.353207440214412 2019-10-01 14_2 1909 15821250 0 0 Oct Q3 2019 22.68583516281303 2019-11-01 14_2 1854 13905589 0 0 Nov Q3 2019 -12.108152010745043 2019-12-01 14_2 2027 13401500 0 0 Dec Q3 2019 -3.625

In [0]:
# Calculate total revenue growth for each district
district_revenue_growth = filtered_df.groupBy('dist_code').agg(F.sum('revenue_growth').alias('total_revenue_growth'))
display(district_revenue_growth)

dist_code total_revenue_growth 14_1 453463.99234715337 14_2 726927.5327551385 14_3 674.4349000992354 14_4 751.4504912816595 14_5 2794.8987890475887 15_1 5432180.5695358785 15_2 1516981.3737488752 15_3 182729.32995479368 16_1 661313.4554226885 17_1 2704.4672341971 17_2 6493134.164211773 17_3 886150.214765546 18_1 500250.9363237695 18_2 987453.97513953 19_1 1147382.2273348556 19_2 3353.1986243893994 19_3 522130.6902364374 19_4 462.3938369060689 20_1 451347.06957180327 20_2 106101.4569334732 20_3 191570.34566496045 20_4 391819.8723811966 21_1 542925.4904653209 21_2 1787.5227677928954 21_3 7391.117024129998 21_5 491.64071155495986 21_6 2506.2948671710906 22_1 499984.6488908369 22_2 96971.24859837782 23_1 1872.8812482392789 23_2 608847.4720896091 23_3 7513.236969784252

In [0]:
# Rank districts based on total revenue growth
ranked_district_code = district_revenue_growth.withColumn('rank', F.rank().over(Window.orderBy(F.col('total_revenue_growth').desc())))

# Select the top 5 district_code
top_5_district_code = ranked_district_code.filter(F.col('rank') <= 5).select('dist_code', 'total_revenue_growth')
display(top_5_district_code)

dist_code total_revenue_growth 17_2 6493134.164211773 15_1 5432180.5695358785 15_2 1516981.3737488752 19_1 1147382.2273348556 18_2 987453.97513953

In [0]:
# Link dist_code to district
top_5_districts = top_5_district_code.join(df1, ['dist_code'])
top_5_districts = top_5_districts.orderBy('total_revenue_growth', ascending=False)
# Display the top 5 districts with the highest revenue growth along with district names
display(top_5_districts)

dist_code total_revenue_growth district 17_2 6493134.164211773 Sangareddy 15_1 5432180.5695358785 Rangareddy 15_2 1516981.3737488752 Medchal_Malkajgiri 19_1 1147382.2273348556 Adilabad 18_2 987453.97513953 Kamareddy

In [0]:
# Convert PySpark DataFrame to Pandas DataFrame
top_5_districts_pd = top_5_districts.toPandas()
top_5_districts_pd

dist_code  total_revenue_growth            district
0      17_2          6.493134e+06          Sangareddy
1      15_1          5.432181e+06          Rangareddy
2      15_2          1.516981e+06  Medchal_Malkajgiri
3      19_1          1.147382e+06            Adilabad
4      18_2          9.874540e+05           Kamareddy

In [0]:
# Create an interactive horizontal bar chart
fig = go.Figure()

fig.add_trace(go.Bar(
    y=top_5_districts_pd['total_revenue_growth'],
    x=top_5_districts_pd['district'],
    orientation='v',
    marker_color='skyblue',
    text=top_5_districts_pd['total_revenue_growth'],
    textposition='inside',
))

fig.update_layout(
    title='Revenue Growth for Top 5 Districts (FY 2019 to 2022)',
    xaxis_title='District',
    yaxis_title='Revenue Growth',
    bargap=0.2,
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
)

# Display the interactive plot in Databricks notebook
display(fig)

In [0]:


# Create an interactive pie chart with color based on district
fig = px.pie(
    top_5_districts_pd,
    names='district',
    values='total_revenue_growth',
    title='Revenue Growth for Top 5 Districts (FY 2019 to 2022)',
    color='district',
    color_discrete_map={district: f"rgba{px.colors.qualitative.Set1[i][3:-1]}, 0.7)" for i, district in enumerate(top_5_districts_pd['district'])},
)

# Display the interactive plot in Databricks notebook
display(fig)

## _Stamp Registration Problem Statement 2 =>_

### How does the revenue generated from document registration compare to the revenue generated from e-stamp challans across districts? List down the top 5 districts where e-stamps revenue contributes significantly more to the revenue than the documents in FY 2022?

In [0]:
# Select relevant columns from df2 for fiscal year information
fiscal_year_df = df2.select('month', 'fiscal_year')

# Select relevant columns from df3 for document registration revenue
doc_reg_df = df3.select('dist_code', 'month', 'documents_registered_rev')

# Join the two DataFrames on 'month'
merged_df = doc_reg_df.join(fiscal_year_df, on='month', how='inner')

# Filter data for fiscal year 2022
filtered_df = merged_df.filter((F.col('fiscal_year') == 2022))

display(filtered_df)


month dist_code documents_registered_rev fiscal_year 2022-04-01 19_1 27857363 2022 2022-04-01 14_1 105448377 2022 2022-04-01 18_2 40413483 2022 2022-04-01 16_1 1211822842 2022 2022-04-01 14_2 31200400 2022 2022-04-01 15_2 2247203989 2022 2022-04-01 22_1 205300353 2022 2022-04-01 21_6 13520532 2022 2022-04-01 14_5 23475205 2022 2022-04-01 18_1 102037591 2022 2022-04-01 14_3 44535076 2022 2022-04-01 17_1 106685105 2022 2022-04-01 23_2 83175309 2022 2022-04-01 15_3 35732768 2022 2022-04-01 21_5 38848963 2022 2022-04-01 23_3 226546587 2022 2022-04-01 17_2 685690327 2022 2022-04-01 15_1 3827108069 2022 2022-04-01 14_4 40005628 2022 2022-04-01 17_3 92665068 2022 2022-04-01 23_1 121359247 2022 2022-04-01 20_4 52079295 2022 2022-04-01 20_3 36241329 2022 2022-04-01 21_3 35414340 2022 2022-04-01 21_2 23073584 2022 2022-04-01 20_1 135392259 2022 2022-04-01 19_2 35864652 2022 2022-04-01 21_1 259104526 2022 2022-04-01 22_2 35456569 2022 2022-04-01 19_4 8021719 2022 2022-04-01 20_2 44513775 2022 2022-04-01 19_3 56079042 2022 2022-05-01 21_2 22950907 2022 2022-05-01 14_3 47900830 2022 2022-05-01 16_1 1021460609 2022 2022-05-01 19_3 54245955 2022 2022-05-01 21_6 15518549 2022 2022-05-01 15_3 48940065 2022 2022-05-01 19_4 5937385 2022 2022-05-01 14_4 49330569 2022 2022-05-01 17_2 633377303 2022 2022-05-01 20_3 35583211 2022 2022-05-01 21_5 35282201 2022 2022-05-01 14_2 30933470 2022 2022-05-01 17_1 60215663 2022 2022-05-01 22_1 214616691 2022 2022-05-01 17_3 73149482 2022 2022-05-01 15_1 3315596443 2022 2022-05-01 19_1 34705198 2022 2022-05-01 18_2 37513866 2022 2022-05-01 22_2 23083026 2022 2022-05-01 14_5 20066197 2022 2022-05-01 14_1 111506589 2022 2022-05-01 20_4 55319046 2022 2022-05-01 21_1 243365485 2022 2022-05-01 23_2 110333900 2022 2022-05-01 18_1 110012852 2022 2022-05-01 20_1 126494603 2022 2022-05-01 23_1 125675316 2022 2022-05-01 23_3 180066950 2022 2022-05-01 15_2 2226604850 2022 2022-05-01 19_2 29781771 2022 2022-05-01 21_3 48228858 2022 2022-05-01 20_2 53618990 2022 2022-06-01 15_3 47477486 2022 2022-06-01 22_2 30536426 2022 2022-06-01 15_2 1974321140 2022 2022-06-01 20_1 127262109 2022 2022-06-01 14_5 17119079 2022 2022-06-01 20_2 50572152 2022 2022-06-01 23_2 97082946 2022 2022-06-01 21_5 42562067 2022 2022-06-01 22_1 190749698 2022 2022-06-01 14_4 29412988 2022 2022-06-01 16_1 1098145933 2022 2022-06-01 21_1 236917721 2022 2022-06-01 21_6 17801739 2022 2022-06-01 19_1 33061858 2022 2022-06-01 23_1 116553271 2022 2022-06-01 18_2 43621441 2022 2022-06-01 14_1 90044509 2022 2022-06-01 21_3 37973277 2022 2022-06-01 18_1 119484825 2022 2022-06-01 20_4 62359926 2022 2022-06-01 19_2 31686371 2022 2022-06-01 14_2 26789974 2022 2022-06-01 17_3 85919031 2022 2022-06-01 21_2 19641045 2022 2022-06-01 23_3 222947172 2022 2022-06-01 15_1 3189161131 2022 2022-06-01 17_2 678801375 2022 2022-06-01 14_3 47414452 2022 2022-06-01 19_3 56935498 2022 2022-06-01 19_4 6122944 2022 2022-06-01 17_1 64355919 2022 2022-06-01 20_3 28917193 2022 2022-07-01 14_4 37222538 2022 2022-07-01 14_1 85214519 2022 2022-07-01 21_6 19927185 2022 2022-07-01 22_2 23931453 2022 2022-07-01 23_3 176853882 2022 2022-07-01 14_3 37936678 2022 2022-07-01 14_2 26238211 2022 2022-07-01 20_2 43309810 2022 2022-07-01 22_1 140282330 2022 2022-07-01 20_4 38040150 2022 2022-07-01 20_3 36197653 2022 2022-07-01 14_5 20197334 2022 2022-07-01 23_1 118724734 2022 2022-07-01 20_1 118665402 2022 2022-07-01 19_3 41714048 2022 2022-07-01 17_2 541290005 2022 2022-07-01 15_1 2787068800 2022 2022-07-01 17_1 42165514 2022 2022-07-01 19_4 5285698 2022 2022-07-01 17_3 77540673 2022 2022-07-01 23_2 78687279 2022 2022-07-01 16_1 1008152412 2022 2022-07-01 21_5 47272385 2022 2022-07-01 18_1 103854975 2022 2022-07-01 21_2 20401003 2022 2022-07-01 19_2 24530135 2022 2022-07-01 21_1 232096281 2022 2022-07-01 15_3 47635696 2022 2022-07-01 19_1 21754906 2022 2022-07-01 15_2 1724072796 2022 2022-07-01 21_3 34217933 2022 2022-07-01 18_2 39274205 2022 2022-08-01 22_2 18804464 2022 2022-08-01 14_1 92104718 

In [0]:
# Select relevant columns from df3 for e-stamp challans revenue
e_stamp_df = df3.select('dist_code', 'month', 'estamps_challans_rev')

# Join the filtered document registration DataFrame with e-stamp DataFrame on 'dist_code' and 'month'
merged_df2 = filtered_df.join(e_stamp_df, on=['dist_code', 'month'], how='inner')

# Calculate the ratio of e-stamps revenue to document registration revenue
merged_df2 = merged_df2.withColumn('estamps_to_docs_ratio', F.col('estamps_challans_rev') / F.col('documents_registered_rev'))

display(merged_df2)

dist_code month documents_registered_rev fiscal_year estamps_challans_rev estamps_to_docs_ratio 19_1 2022-04-01 27857363 2022 21849707 0.7843422580952835 14_1 2022-04-01 105448377 2022 105928140 1.0045497428566397 18_2 2022-04-01 40413483 2022 41078977 1.0164671280621866 16_1 2022-04-01 1211822842 2022 1178763492 0.9727193209649039 14_2 2022-04-01 31200400 2022 31730285 1.0169832758554378 15_2 2022-04-01 2247203989 2022 2179535206 0.9698875654674712 22_1 2022-04-01 205300353 2022 230412276 1.1223179728288144 21_6 2022-04-01 13520532 2022 13433232 0.9935431534794636 14_5 2022-04-01 23475205 2022 23470165 0.9997853053892394 18_1 2022-04-01 102037591 2022 101095524 0.9907674515757628 14_3 2022-04-01 44535076 2022 48755603 1.0947686044141924 17_1 2022-04-01 106685105 2022 66609161 0.6243529591127084 23_2 2022-04-01 83175309 2022 97563368 1.1729847375739837 15_3 2022-04-01 35732768 2022 36942980 1.033868408962888 21_5 2022-04-01 38848963 2022 38941588 1.0023842335251008 23_3 2022-04-01 226546587 2022 229338699 1.0123246703337005 17_2 2022-04-01 685690327 2022 689195855 1.0051124069597674 15_1 2022-04-01 3827108069 2022 3995805965 1.0440797314730859 14_4 2022-04-01 40005628 2022 40225341 1.0054920522682458 17_3 2022-04-01 92665068 2022 90629017 0.9780278475595572 23_1 2022-04-01 121359247 2022 120554337 0.9933675428951863 20_4 2022-04-01 52079295 2022 52919850 1.016139907423862 20_3 2022-04-01 36241329 2022 36531525 1.0080073222480335 21_3 2022-04-01 35414340 2022 35650777 1.0066763068293805 21_2 2022-04-01 23073584 2022 22857614 0.9906399456625378 20_1 2022-04-01 135392259 2022 136515526 1.008296390120797 19_2 2022-04-01 35864652 2022 36164438 1.0083588152479495 21_1 2022-04-01 259104526 2022 246524662 0.9514486906338332 22_2 2022-04-01 35456569 2022 27823990 0.7847344169143946 19_4 2022-04-01 8021719 2022 7365569 0.9182033177676755 20_2 2022-04-01 44513775 2022 45240512 1.0163261147813234 19_3 2022-04-01 56079042 2022 57628834 1.027635850127397 21_2 2022-05-01 22950907 2022 22284377 0.9709584462173979 14_3 2022-05-01 47900830 2022 47346177 0.98842080606954 16_1 2022-05-01 1021460609 2022 1087823055 1.064968189096365 19_3 2022-05-01 54245955 2022 58602240 1.0803061721376277 21_6 2022-05-01 15518549 2022 16755735 1.0797230462719163 15_3 2022-05-01 48940065 2022 47492587 0.9704234557105716 19_4 2022-05-01 5937385 2022 7071065 1.1909392771396836 14_4 2022-05-01 49330569 2022 49386186 1.0011274347960593 17_2 2022-05-01 633377303 2022 633673028 1.0004669017955006 20_3 2022-05-01 35583211 2022 37500026 1.053868522433234 21_5 2022-05-01 35282201 2022 36625583 1.038075345696262 14_2 2022-05-01 30933470 2022 30749220 0.9940436685570678 17_1 2022-05-01 60215663 2022 63395389 1.0528056296581838 22_1 2022-05-01 214616691 2022 196522209 0.915689306755736 17_3 2022-05-01 73149482 2022 68930568 0.9423247590461407 15_1 2022-05-01 3315596443 2022 3307019756 0.9974132295207074 19_1 2022-05-01 34705198 2022 30146408 0.8686424437054069 18_2 2022-05-01 37513866 2022 36639493 0.9766920050308865 22_2 2022-05-01 23083026 2022 24358891 1.055272865871225 14_5 2022-05-01 20066197 2022 21665246 1.079688692381521 14_1 2022-05-01 111506589 2022 116263639 1.0426616045084116 20_4 2022-05-01 55319046 2022 61010707 1.1028879095275794 21_1 2022-05-01 243365485 2022 252150075 1.0360962853873876 23_2 2022-05-01 110333900 2022 97243142 0.8813532558896223 18_1 2022-05-01 110012852 2022 116946832 1.0630288177603104 20_1 2022-05-01 126494603 2022 119127173 0.9417569617574909 23_1 2022-05-01 125675316 2022 124802408 0.9930542605518493 23_3 2022-05-01 180066950 2022 197003851 1.0940589097555105 15_2 2022-05-01 2226604850 2022 1856136612 0.8336174296934635 19_2 2022-05-01 29781771 2022 29056396 0.9756436579946841 21_3 2022-05-01 48228858 2022 47587612 0.986704101515321 20_2 2022-05-01 53618990 2022 54330667 1.0132728535170095 15_3 2022-06-01 47477486 2022 47810409 1.0070122289120362 22_2 2022-06-01 30536426 2022 30610762 1.0024343385830419 15_2 2022-06-01 1974321140 2022 200

In [0]:
# Rank districts based on the ratio in descending order
windowSpec = Window.orderBy(F.col('estamps_to_docs_ratio').desc())
ranked_df = merged_df2.withColumn('rank', F.rank().over(windowSpec))

# Filter for districts with rank <= 5
top_5_districts_code_estamps = ranked_df.filter(F.col('rank') <= 5)

# Show the top districts code where e-stamps revenue contributes significantly more than documents in FY 2022
display(top_5_districts_code_estamps)

dist_code month documents_registered_rev fiscal_year estamps_challans_rev estamps_to_docs_ratio rank 14_5 2022-12-01 21817533 2022 54941667 2.5182346235021162 1 15_3 2022-11-01 43951677 2022 77098216 1.7541586865957355 2 21_3 2023-03-01 34544933 2022 45606428 1.3202060053206646 3 23_3 2023-01-01 155087383 2022 197930372 1.2762506412272105 4 17_1 2022-12-01 49030012 2022 62478201 1.2742848400689766 5

In [0]:
# Select relevant columns from df1 for district names
district_names_df = df1.select('dist_code', 'district')

# Join with df1 to get district names
top_5_districts_estamps = top_5_districts_code_estamps.join(district_names_df, on='dist_code', how='inner')
top_5_districts_estamps = top_5_districts_estamps.orderBy('rank',asc='False')
# Show the top districts where e-stamps revenue contributes significantly more than documents in FY 2022
display(top_5_districts_estamps)

dist_code month documents_registered_rev fiscal_year estamps_challans_rev estamps_to_docs_ratio rank district 14_5 2022-12-01 21817533 2022 54941667 2.5182346235021162 1 Narayanpet 15_3 2022-11-01 43951677 2022 77098216 1.7541586865957355 2 Vikarabad 21_3 2023-03-01 34544933 2022 45606428 1.3202060053206646 3 Jangoan 23_3 2023-01-01 155087383 2022 197930372 1.2762506412272105 4 Yadadri Bhuvanagiri 17_1 2022-12-01 49030012 2022 62478201 1.2742848400689766 5 Medak

In [0]:
# Convert PySpark DataFrame to Pandas DataFrame
top_5_districts_estamps_pd = top_5_districts_estamps.toPandas()
top_5_districts_estamps_pd

dist_code       month  ...  rank             district
0      14_5  2022-12-01  ...     1           Narayanpet
1      15_3  2022-11-01  ...     2            Vikarabad
2      21_3  2023-03-01  ...     3              Jangoan
3      23_3  2023-01-01  ...     4  Yadadri Bhuvanagiri
4      17_1  2022-12-01  ...     5                Medak

[5 rows x 8 columns]

In [0]:
# Create an interactive horizontal bar chart
fig = go.Figure()

fig.add_trace(go.Bar(
    y=top_5_districts_estamps_pd['estamps_to_docs_ratio'],
    x=top_5_districts_estamps_pd['district'],
    orientation='v',
    marker_color='skyblue',
    text=top_5_districts_estamps_pd['estamps_to_docs_ratio'].round(2),
    textposition='inside',
))

fig.update_layout(
    title='Top Districts with High E-stamps to Docs Ratio (FY 2022)',
    yaxis_title='E-stamps to Docs Ratio',
    xaxis_title='District',
    bargap=0.2,
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
)

# Display the interactive plot in Databricks notebook
display(fig)

In [0]:
# Create a pie chart
fig = px.pie(
    top_5_districts_estamps_pd,
    names='district',
    values='estamps_to_docs_ratio',
    title='Top Districts with High E-stamps to Docs Ratio (FY 2022)',
    color='district',
    color_discrete_sequence=px.colors.qualitative.Set1,  # You can choose a different color scale if needed
)

# Show the interactive plot
fig.show()

## _Stamp Registration Problem Statement 3 =>_

### Is there any alteration of e-Stamp challan count and document registration count pattern since the implementation of e-Stamp challan? If so, what suggestions would you propose to the government?

In [0]:
# Select relevant columns for analysis
analysis_df = df3.select('month', 'documents_registered_cnt', 'estamps_challans_cnt')

# Group by month and calculate the total counts
monthly_counts = analysis_df.groupBy('month').agg(
    F.sum('documents_registered_cnt').alias('total_documents_registered'),
    F.sum('estamps_challans_cnt').alias('total_estamps_challans')
).orderBy('month')

display(monthly_counts)


month total_documents_registered total_estamps_challans 2019-04-01 130223 0 2019-05-01 144201 0 2019-06-01 133916 0 2019-07-01 158479 0 2019-08-01 144914 0 2019-09-01 131759 0 2019-10-01 125855 0 2019-11-01 122205 0 2019-12-01 140440 0 2020-01-01 120851 0 2020-02-01 149151 0 2020-03-01 112423 0 2020-04-01 4492 0 2020-05-01 73005 0 2020-06-01 136196 0 2020-07-01 126672 0 2020-08-01 104469 0 2020-09-01 23255 0 2020-10-01 480 0 2020-11-01 277 0 2020-12-01 47019 54241 2021-01-01 147889 153097 2021-02-01 137407 140062 2021-03-01 142732 148732 2021-04-01 107210 111412 2021-05-01 27510 26502 2021-06-01 93591 105664 2021-07-01 123971 134441 2021-08-01 95583 102364 2021-10-01 95766 100475 2021-11-01 96136 101484 2021-12-01 118221 122275 2022-01-01 124221 139513 2022-02-01 101442 101456 2022-03-01 120929 128392 2022-04-01 106000 109522 2022-05-01 104832 109611 2022-06-01 102292 105970 2022-07-01 95846 98843 2022-08-01 92401 96768 2022-09-01 98286 102162 2022-10-01 83444 86507 2022-11-01 100526 105820 2022-12-01 109515 111806 2023-01-01 96256 102968 2023-02-01 101647 104039 2023-03-01 116028 120945

In [0]:
# Convert PySpark DataFrame to Pandas DataFrame
monthly_counts_pd = monthly_counts.toPandas()
monthly_counts_pd.head(5)

month  total_documents_registered  total_estamps_challans
0  2019-04-01                      130223                       0
1  2019-05-01                      144201                       0
2  2019-06-01                      133916                       0
3  2019-07-01                      158479                       0
4  2019-08-01                      144914                       0

In [0]:
# Create a time-series line chart
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=monthly_counts_pd['month'],
    y=monthly_counts_pd['total_documents_registered'],
    mode='lines',
    name='Total Documents Registered',
    line=dict(color='blue')
))

fig.add_trace(go.Scatter(
    x=monthly_counts_pd['month'],
    y=monthly_counts_pd['total_estamps_challans'],
    mode='lines',
    name='Total E-Stamps Challans',
    line=dict(color='orange')
))

fig.update_layout(
    title='Document Registration Count vs. E-Stamp Challan Count Over Time',
    xaxis_title='Month',
    yaxis_title='Count',
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
    
)

# Show the interactive plot
fig.show()

## _Stamp Registration Problem Statement 4 =>_

### Categorize districts into three segments based on their stamp registration revenue generation during the fiscal year 2021 to 2022.


In [0]:
# Select relevant columns for stamp registration revenue and fiscal year
stamp_reg_df = df3.select('dist_code', 'month', 'documents_registered_rev')

# Join with df2 to get the fiscal year column
joined_df = stamp_reg_df.join(df2, stamp_reg_df['month'] == df2['month'], 'inner').drop(df2['month'])

# Filter data for fiscal year 2021 to 2022
filtered_df = joined_df.filter((F.col('fiscal_year') >= 2021) & (F.col('fiscal_year') <= 2022))

# Aggregate total revenue per district
total_revenue_2021_2022 = filtered_df.groupBy('dist_code').agg(F.sum('documents_registered_rev').alias('total_revenue'))

display(total_revenue_2021_2022)


dist_code total_revenue 20_3 744571024 14_1 1960011646 20_2 1069526503 15_1 69563226936 19_3 1086538493 19_4 136257292 23_1 2586636489 14_5 461888320 17_2 14617585438 19_2 633940671 21_5 658996063 20_4 1110412457 17_3 1741861752 23_3 3787070881 21_2 426435218 18_1 2592723703 22_1 3615169800 23_2 1802987342 15_2 42244415731 16_1 24977902615 17_1 1122517735 14_2 601645197 18_2 851578792 15_3 887185451 21_6 364959327 14_4 743833686 19_1 720926384 20_1 2619104284 21_1 4895047216 21_3 733613593 22_2 534180926 14_3 878634232

In [0]:
# Calculate quartiles to categorize districts into segments
quartiles = total_revenue_2021_2022.approxQuantile("total_revenue", [0.33, 0.67], 0.01)

# Categorize districts based on quartiles
categorized_dist_code_stamp_rev_2021_2022 = total_revenue_2021_2022.withColumn(
    'revenue_category',
    F.when(F.col('total_revenue') <= quartiles[0], 'Low Revenue')
    .when((F.col('total_revenue') > quartiles[0]) & (F.col('total_revenue') <= quartiles[1]), 'Medium Revenue')
    .otherwise('High Revenue')
)
 
# Select relevant columns from df1 for district names
district_names_df = df1.select('dist_code', 'district')

# Join with df1 to get district names
categorized_district_stamp_rev_2021_2022 = categorized_dist_code_stamp_rev_2021_2022.join(district_names_df, on='dist_code', how='inner')

# Show the categorized districts
display(categorized_district_stamp_rev_2021_2022)

dist_code total_revenue revenue_category district 20_3 744571024 Medium Revenue Rajanna Sircilla 14_1 1960011646 Medium Revenue Mahabubnagar 20_2 1069526503 Medium Revenue Jagtial 15_1 69563226936 High Revenue Rangareddy 19_3 1086538493 Medium Revenue Mancherial 19_4 136257292 Low Revenue Kumurambheem Asifabad 23_1 2586636489 High Revenue Nalgonda 14_5 461888320 Low Revenue Narayanpet 17_2 14617585438 High Revenue Sangareddy 19_2 633940671 Low Revenue Nirmal 21_5 658996063 Low Revenue Mahabubabad 20_4 1110412457 Medium Revenue Peddapalli 17_3 1741861752 Medium Revenue Siddipet 23_3 3787070881 High Revenue Yadadri Bhuvanagiri 21_2 426435218 Low Revenue Warangal 18_1 2592723703 High Revenue Nizamabad 22_1 3615169800 High Revenue Khammam 23_2 1802987342 Medium Revenue Suryapet 15_2 42244415731 High Revenue Medchal_Malkajgiri 16_1 24977902615 High Revenue Hyderabad 17_1 1122517735 Medium Revenue Medak 14_2 601645197 Low Revenue Jogulamba Gadwal 18_2 851578792 Medium Revenue Kamareddy 15_3 887185451 Medium Revenue Vikarabad 21_6 364959327 Low Revenue Mulugu 14_4 743833686 Low Revenue Wanaparthy 19_1 720926384 Low Revenue Adilabad 20_1 2619104284 High Revenue Karimnagar 21_1 4895047216 High Revenue Hanumakonda 21_3 733613593 Low Revenue Jangoan 22_2 534180926 Low Revenue Bhadradri Kothagudem 14_3 878634232 Medium Revenue Nagarkurnool

In [0]:
# Convert PySpark DataFrame to Pandas DataFrame
categorized_district_stamp_rev_2021_2022_pd = categorized_district_stamp_rev_2021_2022.toPandas()
categorized_district_stamp_rev_2021_2022_pd = categorized_district_stamp_rev_2021_2022_pd.sort_values(by='total_revenue', ascending=False)
categorized_district_stamp_rev_2021_2022_pd.head(5)

dist_code  total_revenue revenue_category            district
3       15_1    69563226936     High Revenue          Rangareddy
18      15_2    42244415731     High Revenue  Medchal_Malkajgiri
19      16_1    24977902615     High Revenue           Hyderabad
8       17_2    14617585438     High Revenue          Sangareddy
28      21_1     4895047216     High Revenue         Hanumakonda

In [0]:

fig = px.bar(categorized_district_stamp_rev_2021_2022_pd,
                                       x = 'district',
                                       y = 'total_revenue',
                                       color = 'revenue_category',
                                       text=categorized_district_stamp_rev_2021_2022_pd['total_revenue'],
                                       color_discrete_map={'Low Revenue': 'red', 'Medium Revenue': 'orange', 'High Revenue': 'green'}
                                       )


fig.update_layout(
    title='Categorized Districts Based on Stamp Registration Revenue (FY 2021 to 2022)',
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
    barmode='stack',  # Stack bars on top of each other
)

# Display the interactive plot in Databricks notebook
display(fig)

# <=Transportation=>

## _Transportation Problem Statement 5 =>_

### Investigate whether there is any correlation between vehicle sales and specific months or seasons in different districts. Are there any months or seasons that consistently show higher or lower sales rate, and if yes, what could be the driving factors? (Consider Fuel-Type category only)

In [0]:
# Select relevant columns
relevant_columns = ['dist_code','month', 'fuel_type_petrol', 'fuel_type_diesel', 'fuel_type_electric', 'fuel_type_others']
fuel_data = df4.select(relevant_columns).withColumn("month_numeric", month(df4["month"]))
display(fuel_data)

dist_code month fuel_type_petrol fuel_type_diesel fuel_type_electric fuel_type_others month_numeric 15_1 2019-04-01 17910 3011 76 22 4 18_2 2019-04-01 3066 306 6 0 4 20_3 2019-04-01 1577 215 0 0 4 21_3 2019-04-01 1961 281 2 0 4 21_7 2019-04-01 1552 309 0 0 4 14_1 2019-04-01 4550 660 0 0 4 17_3 2019-04-01 3112 496 0 0 4 14_3 2019-04-01 2200 496 0 0 4 19_2 2019-04-01 1736 263 2 9 4 14_2 2019-04-01 2033 173 0 0 4 20_4 2019-04-01 2066 350 4 5 4 15_3 2019-04-01 3636 877 6 2 4 19_3 2019-04-01 2006 367 9 14 4 23_1 2019-04-01 4656 744 2 12 4 23_2 2019-04-01 3295 676 1 2 4 20_2 2019-04-01 2786 440 2 0 4 23_3 2019-04-01 2468 470 2 12 4 20_1 2019-04-01 3028 579 0 15 4 16_1 2019-04-01 24309 2957 284 1540 4 15_2 2019-04-01 19273 3634 42 16 4 17_2 2019-04-01 5291 1115 25 8 4 17_1 2019-04-01 2240 439 2 0 4 18_1 2019-04-01 4701 772 2 22 4 14_4 2019-04-01 1752 262 0 0 4 22_1 2019-04-01 5740 760 4 49 4 21_5 2019-04-01 1945 297 1 2 4 22_2 2019-04-01 3527 669 2 4 4 19_1 2019-04-01 1758 326 0 2 4 21_2 2019-04-01 5371 999 3 6 4 19_4 2019-04-01 1149 155 0 0 4 21_2 2019-05-01 6101 988 7 10 5 19_1 2019-05-01 1870 190 0 9 5 22_2 2019-05-01 3364 828 2 2 5 21_5 2019-05-01 2126 415 0 0 5 22_1 2019-05-01 4989 926 0 56 5 18_1 2019-05-01 5795 900 4 25 5 15_2 2019-05-01 18836 3695 69 47 5 17_2 2019-05-01 5458 1157 5 2 5 16_1 2019-05-01 24949 3035 83 1755 5 14_4 2019-05-01 1587 298 0 0 5 15_1 2019-05-01 17962 3280 76 27 5 23_3 2019-05-01 2404 595 0 16 5 17_1 2019-05-01 2134 453 0 0 5 20_1 2019-05-01 2846 753 0 14 5 19_4 2019-05-01 963 163 2 0 5 23_1 2019-05-01 5141 1103 4 12 5 20_3 2019-05-01 1639 207 4 0 5 21_3 2019-05-01 1617 313 0 0 5 21_7 2019-05-01 1741 344 0 0 5 14_1 2019-05-01 3975 823 4 2 5 17_3 2019-05-01 3338 603 2 0 5 14_3 2019-05-01 1816 470 0 0 5 18_2 2019-05-01 3080 378 10 2 5 19_2 2019-05-01 2424 276 0 8 5 19_3 2019-05-01 1899 471 7 9 5 15_3 2019-05-01 4075 954 4 0 5 23_2 2019-05-01 4823 879 0 0 5 14_2 2019-05-01 1684 193 0 0 5 20_2 2019-05-01 2907 541 0 0 5 20_4 2019-05-01 1893 374 4 2 5 23_3 2019-06-01 2257 652 2 14 6 21_2 2019-06-01 5365 1275 16 10 6 19_1 2019-06-01 1384 243 0 2 6 22_2 2019-06-01 2865 989 2 2 6 21_5 2019-06-01 1746 521 0 2 6 22_1 2019-06-01 4476 1114 4 54 6 18_1 2019-06-01 5427 1001 10 28 6 17_1 2019-06-01 1908 548 4 2 6 15_1 2019-06-01 19367 3656 95 35 6 15_2 2019-06-01 20110 3961 60 39 6 16_1 2019-06-01 28578 3210 58 1696 6 14_4 2019-06-01 1517 460 0 0 6 20_1 2019-06-01 2950 816 8 18 6 19_4 2019-06-01 741 174 0 0 6 17_2 2019-06-01 5119 1386 35 5 6 23_2 2019-06-01 3432 1055 0 0 6 19_3 2019-06-01 1892 604 0 8 6 23_1 2019-06-01 4514 1163 2 30 6 18_2 2019-06-01 2783 468 8 2 6 20_3 2019-06-01 1493 293 0 0 6 21_3 2019-06-01 1381 342 0 0 6 14_1 2019-06-01 3619 897 6 0 6 17_3 2019-06-01 3279 699 6 4 6 21_7 2019-06-01 1571 637 0 0 6 19_2 2019-06-01 1705 394 2 10 6 20_2 2019-06-01 3173 697 0 0 6 14_2 2019-06-01 1751 220 0 0 6 20_4 2019-06-01 2070 511 8 2 6 15_3 2019-06-01 3203 830 2 4 6 14_3 2019-06-01 1818 515 0 0 6 20_2 2019-07-01 2997 461 0 2 7 19_3 2019-07-01 1615 419 10 10 7 15_3 2019-07-01 3027 865 4 4 7 20_4 2019-07-01 1649 370 0 5 7 14_2 2019-07-01 1861 165 2 0 7 19_2 2019-07-01 1431 278 0 9 7 18_2 2019-07-01 2144 354 0 4 7 17_3 2019-07-01 2781 525 0 2 7 14_1 2019-07-01 3578 716 2 0 7 21_7 2019-07-01 1581 490 1 0 7 21_3 2019-07-01 1318 247 0 2 7 20_3 2019-07-01 1230 224 0 0 7 23_1 2019-07-01 4398 956 2 71 7 14_3 2019-07-01 1970 482 0 0 7 23_2 2019-07-01 3144 803 0 2 7 20_1 2019-07-01 2745 528 0 25 7 23_3 2019-07-01 2363 437 0 72 7 14_4 2019-07-01 1524 318 0 0 7 16_1 2019-07-01 26435 2937 79 2326 7 15_2 2019-07-01 19433 3484 155 53 7 17_2 2019-07-01 4687 1186 42 5 7 17_1 2019-07-01 1550 414 0 0 7 18_1 2019-07-01 4391 782 10 24 7 15_1 2019-07-01 18266 3038 72 39 7 22_1 2019-07-01 4114 714 0 41 7 21_5 2019-07-01 1664 436 0 0 7 22_2 2019-07-01 2767 650 0 2 7 19_1 2019-07-01 1264 197 0 9 7 21_2 2019-07-01 4805 929 2 10 7 19_4 2019-07-01 717 145 2 0 7 23_1 2019-08-01 3821 809 5 58 8 19_3 2019-08-01 1730 458 2 8 8 15_3 2019-08-01 25

In [0]:
fuel_data2 = fuel_data.groupBy('month_numeric').agg(
    sum('fuel_type_petrol').alias('sum_fuel_type_petrol'),
    sum('fuel_type_diesel').alias('sum_fuel_type_diesel'),
    sum('fuel_type_electric').alias('sum_fuel_type_electric'),
    sum('fuel_type_others').alias('sum_fuel_type_others')
).orderBy('month_numeric', asc = True)

display(fuel_data2)

month_numeric sum_fuel_type_petrol sum_fuel_type_diesel sum_fuel_type_electric sum_fuel_type_others 1 461802 83417 11431 7841 2 437066 80949 10366 7062 3 483165 87782 17390 12121 4 358884 59739 7127 4973 5 364607 65556 4384 4648 6 508584 93581 5797 5452 7 465809 79271 6992 6920 8 482193 69282 9177 8399 9 417136 75262 8981 9452 10 631877 101603 7603 7729 11 497327 74429 7458 7162 12 414815 78513 6953 7710

In [0]:
fuel_data_pd = fuel_data2.toPandas()
fuel_data_pd


month_numeric  ...  sum_fuel_type_others
0               1  ...                  7841
1               2  ...                  7062
2               3  ...                 12121
3               4  ...                  4973
4               5  ...                  4648
5               6  ...                  5452
6               7  ...                  6920
7               8  ...                  8399
8               9  ...                  9452
9              10  ...                  7729
10             11  ...                  7162
11             12  ...                  7710

[12 rows x 5 columns]

In [0]:
fuel_data_pd_corr = fuel_data_pd.corr()
fuel_data_pd_corr

month_numeric  ...  sum_fuel_type_others
month_numeric                1.000000  ...              0.023742
sum_fuel_type_petrol         0.289317  ...              0.305088
sum_fuel_type_diesel         0.063162  ...              0.339557
sum_fuel_type_electric      -0.446722  ...              0.855317
sum_fuel_type_others         0.023742  ...              1.000000

[5 rows x 5 columns]

In [0]:
# Create the heatmap using the correlation matrix
fig = ff.create_annotated_heatmap(
    z=fuel_data_pd_corr.values,
    x=list(fuel_data_pd_corr.columns),
    y=list(fuel_data_pd_corr.index),
    colorscale='inferno',
    annotation_text=fuel_data_pd_corr.values.round(3),
)

# Update the layout for better presentation
fig.update_layout(
    title='Correlation Matrix Heatmap Fuel-Type category',
    xaxis=dict(ticks='', side='bottom'),
    yaxis=dict(ticks='', tickvals=list(range(len(fuel_data_pd_corr.index))), ticktext=list(fuel_data_pd_corr.index))
)

In [0]:
# Create a time-series line chart
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=fuel_data_pd['month_numeric'],
    y=fuel_data_pd['sum_fuel_type_petrol'],
    mode='lines',
    name='Total Petrol Sales',
    line=dict(color='yellow')
))

fig.add_trace(go.Scatter(
    x=fuel_data_pd['month_numeric'],
    y=fuel_data_pd['sum_fuel_type_diesel'],
    mode='lines',
    name='Total Diesel Sales',
    line=dict(color='blue')
))

fig.add_trace(go.Scatter(
    x=fuel_data_pd['month_numeric'],
    y=fuel_data_pd['sum_fuel_type_electric'],
    mode='lines',
    name='Total Electric Sales',
    line=dict(color='green')
))

fig.add_trace(go.Scatter(
    x=fuel_data_pd['month_numeric'],
    y=fuel_data_pd['sum_fuel_type_others'],
    mode='lines',
    name='Total Other Fuel Sales',
    line=dict(color='orange')
))

fig.update_layout(
    title="Fuel Type's Trend",
    xaxis_title='Month Numeric',
    yaxis_title='Fuel Sum',
    xaxis=dict(showgrid=False, tickmode = 'array' ,tickvals=fuel_data_pd['month_numeric'].unique()), # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
    
)

# Show the interactive plot
fig.show()

## _Transportation Problem Statement 6 =>_

### How does the distribution of vehicles vary by vehicle class (MotorCycle, MotorCar, AutoRickshaw, Agriculture) across different districts? Are there any districts with a predominant preference for a specific vehicle class? Consider FY 2022 for analysis.

In [0]:
relevant_columns=['dist_code', 'month', 'vehicleClass_MotorCycle', 'vehicleClass_MotorCar', 'vehicleClass_AutoRickshaw', 'vehicleClass_Agriculture', 'vehicleClass_others']
vclass = df4.select(relevant_columns)
# Filter data based on fiscal years in df2
filtered_df = vclass.join(df2['month', 'fiscal_year'], ['month']).filter((col('fiscal_year') == 2022)).drop('month')
display(filtered_df)

dist_code vehicleClass_MotorCycle vehicleClass_MotorCar vehicleClass_AutoRickshaw vehicleClass_Agriculture vehicleClass_others fiscal_year 14_4 872 106 10 50 228 2022 21_7 1211 127 16 129 55 2022 14_1 2004 283 26 74 294 2022 17_3 1834 311 22 213 257 2022 14_3 1356 184 11 88 261 2022 19_2 1441 176 20 60 91 2022 20_2 1547 250 26 65 38 2022 14_2 1055 94 2 63 217 2022 20_4 1147 271 13 40 92 2022 15_3 3067 557 53 184 161 2022 19_3 1502 230 26 18 246 2022 23_1 2588 446 26 180 251 2022 23_2 1814 273 36 111 403 2022 20_1 1948 522 43 57 1790 2022 21_3 961 106 14 94 75 2022 21_2 1845 298 59 38 114 2022 19_1 1450 129 18 29 109 2022 22_2 2161 301 94 170 224 2022 21_5 1223 124 23 65 217 2022 22_1 2898 554 170 174 202 2022 19_4 959 78 12 6 94 2022 18_1 2865 634 54 75 520 2022 17_1 1536 263 25 96 145 2022 17_2 4182 1382 112 108 499 2022 15_2 16027 5872 4 18 1440 2022 16_1 18533 4481 751 2 1280 2022 15_1 13642 6463 8 13 1125 2022 23_3 1463 276 8 96 177 2022 20_3 856 146 6 47 93 2022 18_2 1795 205 9 54 236 2022 18_2 1731 180 16 59 604 2022 16_1 17705 4735 689 2 1099 2022 15_2 13966 5521 0 26 1620 2022 17_2 4078 1299 137 109 393 2022 17_1 1152 211 40 143 170 2022 18_1 3011 612 44 105 319 2022 19_4 654 41 25 6 225 2022 22_1 2575 593 203 312 323 2022 21_5 972 114 39 128 255 2022 22_2 1367 272 67 240 230 2022 19_1 1123 151 25 30 176 2022 21_2 1673 333 79 81 310 2022 23_3 1338 349 19 249 160 2022 20_1 1800 451 67 194 2355 2022 23_2 1723 310 30 245 392 2022 19_3 1100 227 20 15 121 2022 15_3 2566 564 84 147 307 2022 20_4 965 228 25 52 77 2022 14_2 924 80 5 79 129 2022 20_2 1399 200 18 54 186 2022 19_2 1383 156 14 51 248 2022 14_3 1197 208 22 179 291 2022 17_3 1582 299 13 271 194 2022 14_1 1733 280 39 80 341 2022 21_7 759 106 15 170 244 2022 21_3 769 111 14 139 146 2022 20_3 736 127 12 69 97 2022 23_1 2550 454 20 351 488 2022 14_4 874 83 16 87 134 2022 15_1 13286 6347 2 29 1374 2022 15_1 16312 7009 0 42 2590 2022 18_2 1471 209 17 106 225 2022 20_3 848 132 7 111 91 2022 21_3 880 107 27 229 123 2022 21_7 799 112 18 284 238 2022 14_1 1771 313 81 142 275 2022 17_3 1736 342 27 444 211 2022 14_3 1063 194 29 180 405 2022 20_2 1517 222 12 109 173 2022 14_2 866 78 8 87 114 2022 20_4 1212 208 25 136 160 2022 15_3 2557 552 180 232 260 2022 19_3 1119 235 20 46 151 2022 23_1 2443 486 33 413 545 2022 23_2 1830 345 47 437 509 2022 19_2 964 141 15 98 121 2022 23_3 1431 340 9 268 362 2022 20_1 1976 475 60 148 1684 2022 14_4 782 128 26 127 128 2022 16_1 20321 5332 743 2 1887 2022 15_2 16529 6076 0 31 2095 2022 17_2 4039 1341 127 220 411 2022 18_1 2750 562 79 155 283 2022 17_1 1156 223 23 377 323 2022 22_1 2584 578 252 379 527 2022 21_5 1060 114 54 195 257 2022 22_2 1532 319 83 353 276 2022 19_1 780 152 47 14 136 2022 21_2 1762 297 76 106 284 2022 19_4 509 37 12 16 117 2022 19_1 883 121 40 15 91 2022 19_4 335 41 6 12 86 2022 22_2 1159 277 76 139 362 2022 21_5 923 122 58 102 182 2022 22_1 2019 553 243 179 585 2022 18_1 2118 430 88 82 181 2022 18_2 1103 160 26 62 149 2022 17_2 3506 1263 170 124 449 2022 15_2 14425 5649 0 31 1901 2022 16_1 18524 5147 589 6 1710 2022 14_4 778 106 31 108 134 2022 15_1 13733 6922 6 40 1933 2022 21_2 1419 234 100 79 199 2022 17_1 834 191 29 140 191 2022 23_3 1202 389 24 153 247 2022 20_2 1074 195 12 103 86 2022 23_2 1569 251 52 230 356 2022 20_1 1532 377 101 99 1443 2022 21_3 772 91 18 120 130 2022 21_7 662 110 14 199 90 2022 14_1 1732 358 59 115 274 2022 17_3 1387 299 40 277 157 2022 14_3 1204 199 20 143 303 2022 20_3 478 93 6 42 78 2022 14_2 918 81 8 106 118 2022 20_4 743 143 16 76 151 2022 15_3 1966 496 129 176 262 2022 19_3 725 188 23 68 180 2022 23_1 2402 442 68 236 405 2022 19_2 855 134 34 64 84 2022 23_3 1389 338 38 79 208 2022 21_2 1854 292 151 37 104 2022 19_1 757 138 30 23 108 2022 22_2 1471 284 54 116 166 2022 21_5 967 121 82 26 136 2022 22_1 2677 561 253 135 148 2022 19_4 424 52 22 7 62 2022 17_2 3833 1543 327 79 556 2022 17_1 1027 251 63 75 152 2022 15_2 16617 6225 8 16 1864 2022 16_1 22585 5331 981 6 1529 2022 14_4 765 115 32 69 

In [0]:
# Sum the counts of vehicles for each vehicle class and district
vclass_dist_code = filtered_df.groupby(['dist_code']).agg(
    sum('vehicleClass_MotorCycle').alias('sum_vehicleClass_MotorCycle'),
    sum('vehicleClass_MotorCar').alias('sum_vehicleClass_MotorCar'),
    sum('vehicleClass_AutoRickshaw').alias('sum_vehicleClass_AutoRickshaw'),
    sum('vehicleClass_Agriculture').alias('sum_vehicleClass_Agriculture')
).orderBy('dist_code', asc = True)

# Show the resulting DataFrame
display(vclass_dist_code)

dist_code sum_vehicleClass_MotorCycle sum_vehicleClass_MotorCar sum_vehicleClass_AutoRickshaw sum_vehicleClass_Agriculture 14_1 17977 3300 1130 937 14_2 10300 899 116 868 14_3 12229 2066 366 1556 14_4 8771 1194 372 985 15_1 154186 71832 69 449 15_2 164626 61071 83 261 15_3 23116 5211 2046 1814 16_1 206819 51447 8397 20 17_1 11663 2347 610 1579 17_2 40784 14565 3381 1570 17_3 17401 3254 524 2437 18_1 28105 5824 1011 1181 18_2 15184 2153 379 748 19_1 10410 1416 368 467 19_2 10984 1581 295 989 19_3 11603 2218 550 400 19_4 6433 479 286 160 20_1 19411 4818 1042 999 20_2 13639 2055 272 858 20_3 8007 1376 148 675 20_4 10818 2205 382 705 21_2 17770 2937 1331 681 21_3 8617 1177 397 1225 21_5 11046 1155 680 906 21_7 9225 1343 218 1928 22_1 27385 5880 2690 2121 22_2 17022 3157 1388 2013 23_1 27942 4927 964 2599 23_2 19165 3038 739 2188 23_3 14471 3216 465 1853

In [0]:
vclass_district = vclass_dist_code.join(df1,'dist_code')
display(vclass_district)

dist_code sum_vehicleClass_MotorCycle sum_vehicleClass_MotorCar sum_vehicleClass_AutoRickshaw sum_vehicleClass_Agriculture district 20_3 8007 1376 148 675 Rajanna Sircilla 14_1 17977 3300 1130 937 Mahabubnagar 20_2 13639 2055 272 858 Jagtial 15_1 154186 71832 69 449 Rangareddy 19_3 11603 2218 550 400 Mancherial 19_4 6433 479 286 160 Kumurambheem Asifabad 23_1 27942 4927 964 2599 Nalgonda 17_2 40784 14565 3381 1570 Sangareddy 19_2 10984 1581 295 989 Nirmal 21_5 11046 1155 680 906 Mahabubabad 20_4 10818 2205 382 705 Peddapalli 17_3 17401 3254 524 2437 Siddipet 23_3 14471 3216 465 1853 Yadadri Bhuvanagiri 21_2 17770 2937 1331 681 Warangal 18_1 28105 5824 1011 1181 Nizamabad 22_1 27385 5880 2690 2121 Khammam 23_2 19165 3038 739 2188 Suryapet 15_2 164626 61071 83 261 Medchal_Malkajgiri 16_1 206819 51447 8397 20 Hyderabad 17_1 11663 2347 610 1579 Medak 14_2 10300 899 116 868 Jogulamba Gadwal 18_2 15184 2153 379 748 Kamareddy 15_3 23116 5211 2046 1814 Vikarabad 14_4 8771 1194 372 985 Wanaparthy 19_1 10410 1416 368 467 Adilabad 20_1 19411 4818 1042 999 Karimnagar 21_7 9225 1343 218 1928 Jayashankar Bhupalpally 21_3 8617 1177 397 1225 Jangoan 22_2 17022 3157 1388 2013 Bhadradri Kothagudem 14_3 12229 2066 366 1556 Nagarkurnool

In [0]:
vclass_district_pd = vclass_district.toPandas()
vclass_district_pd.head(5)

dist_code  ...          district
0      20_3  ...  Rajanna Sircilla
1      14_1  ...      Mahabubnagar
2      20_2  ...           Jagtial
3      15_1  ...        Rangareddy
4      19_3  ...        Mancherial

[5 rows x 6 columns]

In [0]:
import plotly.graph_objects as go

# Visualize the distribution using a bar chart
fig = go.Figure()

fig.add_trace(go.Bar(
    x=vclass_district_pd['district'],
    y=vclass_district_pd['sum_vehicleClass_MotorCycle'],
    name='MotorCycle',
    text=vclass_district_pd['sum_vehicleClass_MotorCycle'],  # Add text inside the bars
    marker_color='blue'
))

fig.add_trace(go.Bar(
    x=vclass_district_pd['district'],
    y=vclass_district_pd['sum_vehicleClass_MotorCar'],
    name='MotorCar',
    text=vclass_district_pd['sum_vehicleClass_MotorCar'],
    marker_color='orange'
))

fig.add_trace(go.Bar(
    x=vclass_district_pd['district'],
    y=vclass_district_pd['sum_vehicleClass_AutoRickshaw'],
    name='AutoRickshaw',
    text=vclass_district_pd['sum_vehicleClass_AutoRickshaw'],
    marker_color='yellow'
))

fig.add_trace(go.Bar(
    x=vclass_district_pd['district'],
    y=vclass_district_pd['sum_vehicleClass_Agriculture'],
    name='Agriculture',
    text=vclass_district_pd['sum_vehicleClass_Agriculture'],
    marker_color='green'
))

fig.update_layout(
    title='Distribution of Vehicles by Vehicle Class (FY 2022)',
    barmode='stack',  # Stack bars on top of each other
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
)

# Show the interactive plot
fig.show()


## _Transportation Problem Statement 7 =>_

### List down the top 3 and bottom 3 districts that have shown the highest and lowest vehicle sales growth during FY 2022 compared to FY 2021? (Consider and compare categories: Petrol, Diesel and Electric)

In [0]:
# Select relevant columns
relevant_columns = ['dist_code', 'month', 'fuel_type_petrol', 'fuel_type_diesel', 'fuel_type_electric']
fuel_data_2021_2022 = df4.select(relevant_columns).join(df2.select('month', 'fiscal_year'), 'month')\
              .filter((col('fiscal_year') >= 2021) & (col('fiscal_year') <= 2022))\
              .drop('month')

# Display the result
display(fuel_data_2021_2022)

dist_code fuel_type_petrol fuel_type_diesel fuel_type_electric fiscal_year 21_3 990 285 0 2021 21_7 1750 360 10 2021 14_1 3301 661 19 2021 17_3 1893 474 6 2021 14_3 1718 539 2 2021 19_2 1719 192 6 2021 20_2 1858 258 12 2021 14_2 1339 234 0 2021 20_4 1349 278 6 2021 15_3 3287 530 10 2021 19_3 1778 261 0 2021 23_1 3224 724 6 2021 23_2 2258 606 2 2021 20_3 1073 195 2 2021 18_2 2120 253 8 2021 21_2 4136 644 20 2021 15_1 14342 1948 240 2021 14_4 1174 238 2 2021 16_1 17679 1890 227 2021 15_2 16798 2259 242 2021 23_3 1711 398 8 2021 17_1 1458 315 2 2021 17_2 4669 627 50 2021 19_4 876 130 0 2021 22_1 3757 749 2 2021 21_5 1880 423 0 2021 22_2 2697 503 3 2021 19_1 1554 123 2 2021 18_1 3516 474 49 2021 20_1 2061 435 2 2021 14_4 606 152 0 2021 18_2 1656 149 0 2021 15_1 7008 1006 86 2021 20_2 1202 191 2 2021 20_3 669 131 20 2021 21_3 566 259 2 2021 21_7 808 282 2 2021 14_1 2068 419 4 2021 17_3 1147 322 2 2021 14_3 948 404 0 2021 19_2 1336 137 0 2021 14_2 803 147 0 2021 20_4 893 186 0 2021 15_3 2111 324 2 2021 23_1 1708 615 2 2021 23_2 1235 498 0 2021 19_3 724 143 0 2021 23_3 853 310 2 2021 16_1 8242 778 101 2021 15_2 7704 1130 98 2021 17_2 2628 398 11 2021 17_1 900 252 0 2021 20_1 1074 278 3 2021 19_4 486 73 0 2021 18_1 2611 329 4 2021 21_5 1157 373 0 2021 22_2 1578 417 0 2021 19_1 1092 67 2 2021 21_2 2232 558 8 2021 22_1 1897 560 0 2021 23_3 2053 590 12 2021 21_5 2085 698 0 2021 21_2 4585 1107 19 2021 19_1 1262 126 7 2021 22_2 2576 691 0 2021 22_1 3763 1035 2 2021 14_4 1325 338 4 2021 18_1 4889 682 54 2021 17_1 1836 857 9 2021 17_2 4694 722 41 2021 15_2 15387 1925 292 2021 20_1 2746 636 23 2021 19_4 745 112 2 2021 23_2 2552 1178 6 2021 18_2 3115 441 19 2021 19_3 1740 344 0 2021 15_3 3448 531 10 2021 20_4 1958 468 3 2021 14_2 1463 233 7 2021 20_2 2907 444 2 2021 19_2 2044 314 4 2021 14_3 2172 604 0 2021 17_3 3037 938 43 2021 14_1 3819 809 7 2021 21_7 1669 739 2 2021 21_3 1328 554 0 2021 20_3 1419 354 20 2021 16_1 16348 1606 515 2021 23_1 3760 1213 8 2021 15_1 13192 1645 225 2021 20_1 2310 411 26 2021 22_1 3898 855 2 2021 15_1 15406 2322 344 2021 18_2 2359 298 12 2021 14_4 1260 314 9 2021 16_1 19156 1754 465 2021 15_2 17169 2447 492 2021 17_2 4410 640 147 2021 17_1 1727 418 18 2021 18_1 4589 491 135 2021 19_4 692 121 2 2021 21_5 1967 501 0 2021 22_2 2502 563 4 2021 19_1 1327 147 22 2021 23_3 2253 491 6 2021 21_2 4692 849 33 2021 19_2 1836 217 18 2021 23_1 4124 886 6 2021 19_3 1629 353 20 2021 15_3 3168 639 34 2021 20_4 1565 297 13 2021 14_2 1549 255 4 2021 20_2 2667 303 14 2021 23_2 2956 922 8 2021 14_3 1666 584 4 2021 17_3 2717 548 48 2021 14_1 3183 748 15 2021 21_7 1814 552 2 2021 21_3 1409 321 4 2021 20_3 1253 205 24 2021 23_2 2528 489 18 2021 20_1 2911 339 23 2021 21_2 4721 581 47 2021 23_1 3397 591 3 2021 23_3 2199 374 13 2021 19_3 1724 201 10 2021 17_3 2573 387 46 2021 20_4 1800 264 20 2021 14_2 1288 178 8 2021 20_2 2509 231 37 2021 19_1 1303 190 8 2021 19_2 1650 257 26 2021 15_3 3121 470 27 2021 22_2 2198 415 2 2021 18_2 2217 268 7 2021 22_1 3897 593 6 2021 19_4 669 123 0 2021 18_1 4529 504 126 2021 17_1 1521 355 24 2021 17_2 4454 557 86 2021 15_2 18152 2370 448 2021 16_1 20094 1975 609 2021 14_4 1291 219 12 2021 15_1 16192 2254 305 2021 14_1 3409 551 20 2021 21_7 1463 250 8 2021 21_3 1285 235 2 2021 20_3 1667 155 23 2021 21_5 1597 234 0 2021 14_3 1657 403 6 2021 23_2 2012 608 16 2021 14_4 836 196 7 2021 15_1 13649 1937 314 2021 18_2 1638 232 4 2021 20_3 991 157 54 2021 21_3 1154 269 4 2021 21_7 1069 249 6 2021 14_1 1565 330 25 2021 17_3 1941 442 34 2021 14_3 1208 425 5 2021 20_2 1756 285 23 2021 14_2 808 125 2 2021 20_4 1267 265 12 2021 15_3 2385 466 45 2021 19_3 1534 240 19 2021 19_2 1163 223 42 2021 20_1 2317 350 68 2021 16_1 17928 1546 551 2021 23_1 2621 578 29 2021 17_2 3566 609 106 2021 17_1 1260 400 5 2021 18_1 3123 485 105 2021 19_4 527 121 4 2021 15_2 14553 2016 422 2021 21_5 1165 293 0 2021 23_3 1575 401 12 2021 22_2 1552 368 4 2021 19_1 862 155 36 2021 21_2 1909 280 23 2021 22_1 3141 549 4 2021 19_1 1958 324 34 2021 22_2 3

In [0]:
# Define relevant columns
relevant_columns = ['dist_code', 'fuel_type_petrol', 'fuel_type_diesel', 'fuel_type_electric']

# Define a window specification to order data by district and fuel type within each fiscal year
window_spec = Window.partitionBy('dist_code').orderBy('fiscal_year')

# Calculate the lagged sales to compare with the previous fiscal year for all fuel types
for fuel_type in ['petrol', 'diesel', 'electric']:
    fuel_data_2021_2022 = fuel_data_2021_2022.withColumn(f'lagged_sales_{fuel_type}', lag(f'fuel_type_{fuel_type}').over(window_spec))

# Calculate sales growth for all fuel types
for fuel_type in ['petrol', 'diesel', 'electric']:
    fuel_data_2021_2022 = fuel_data_2021_2022.withColumn(f'sales_growth_{fuel_type}',
                                                         (col(f'fuel_type_{fuel_type}') - col(f'lagged_sales_{fuel_type}')) /
                                                         col(f'lagged_sales_{fuel_type}') * 100)

# Drop unnecessary columns
for fuel_type in ['petrol', 'diesel', 'electric']:
    fuel_data_2021_2022 = fuel_data_2021_2022.drop(f'lagged_sales_{fuel_type}')

# Fill null values with 0
fuel_data_2021_2022 = fuel_data_2021_2022.fillna(0)

# Group by 'dist_code' before joining with df1
grouped_fuel_data = fuel_data_2021_2022.groupBy(['dist_code','fiscal_year']).agg(
    {'sales_growth_petrol': 'avg', 'sales_growth_diesel': 'avg', 'sales_growth_electric': 'avg'}
)

# Join with df1
ranked_data = grouped_fuel_data.join(df1, 'dist_code').drop('dist_code')

# Rank districts based on average sales growth for each fuel type
ranked_data_petrol = ranked_data.withColumn('rank_petrol', dense_rank().over(Window.orderBy(desc('avg(sales_growth_petrol)'))))
ranked_data_diesel = ranked_data.withColumn('rank_diesel', dense_rank().over(Window.orderBy(desc('avg(sales_growth_diesel)'))))
ranked_data_electric = ranked_data.withColumn('rank_electric', dense_rank().over(Window.orderBy(desc('avg(sales_growth_electric)'))))

# Select the top and bottom 3 districts for each fuel type
top_3_petrol = ranked_data_petrol.filter(col('rank_petrol') <= 3).select('district', 'avg(sales_growth_petrol)')
bottom_3_petrol = ranked_data_petrol.filter(col('rank_petrol') > (ranked_data_petrol.count() - 3)).select('district', 'avg(sales_growth_petrol)')

top_3_diesel = ranked_data_diesel.filter(col('rank_diesel') <= 3).select('district', 'avg(sales_growth_diesel)')
bottom_3_diesel = ranked_data_diesel.filter(col('rank_diesel') > (ranked_data_diesel.count() - 3)).select('district', 'avg(sales_growth_diesel)')

top_3_electric = ranked_data_electric.filter(col('rank_electric') <= 3).select('district', 'avg(sales_growth_electric)')
bottom_3_electric = ranked_data_electric.filter(col('rank_electric') > (ranked_data_electric.count() - 3)).select('district', 'avg(sales_growth_electric)')


In [0]:
# Display the results for petrol fuel type
print("Top 3 District with Highest Petrol Sales Growth:")
display(top_3_petrol)

print("Bottom 3 District with Lowest Petrol Sales Growth:")
display(bottom_3_petrol)

Top 3 District with Highest Petrol Sales Growth:


district avg(sales_growth_petrol) Kumurambheem Asifabad 20.053877538836343 Vikarabad 18.995660385556228 Jogulamba Gadwal 13.718284015423409

Bottom 3 District with Lowest Petrol Sales Growth:


district avg(sales_growth_petrol) Warangal 2.3980680899531417 Jayashankar Bhupalpally 2.3812553952178273 Mahabubabad 2.3596243368311214

In [0]:
top_3_petrol_pd = top_3_petrol.toPandas()
bottom_3_petrol_pd = bottom_3_petrol.toPandas()

# Plot the results using Plotly

fig_top = px.bar(top_3_petrol_pd,
                  x='district', 
                  y='avg(sales_growth_petrol)', 
                  title='Top 3 Districts - Petrol Sales Growth',
                  text=top_3_petrol_pd['avg(sales_growth_petrol)']
)

fig_top.update_layout(
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
)

fig_bottom = px.bar(bottom_3_petrol_pd, 
                    x='district', 
                    y='avg(sales_growth_petrol)',
                    
                    title='Bottom 3 Districts - Petrol Sales Growth',
                    text=bottom_3_petrol_pd['avg(sales_growth_petrol)']
)

fig_bottom.update_traces(marker_color='red')

fig_bottom.update_layout(
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
)

# Display the plots
fig_top.show()
fig_bottom.show()

In [0]:
# Display the results for diesel fuel type
print("Top 3 District with Highest Diesel Sales Growth:")
display(top_3_diesel)

print("Bottom 3 District with Lowest Diesel Sales Growth:")
display(bottom_3_diesel)

Top 3 District with Highest Diesel Sales Growth:


district avg(sales_growth_diesel) Jogulamba Gadwal 24.569502448182348 Adilabad 19.54651070106296 Kumurambheem Asifabad 15.849645858912245

Bottom 3 District with Lowest Diesel Sales Growth:


district avg(sales_growth_diesel) Mahabubabad 2.9221345186161565 Jangoan 1.6241254874640842 Warangal -0.4860455792027314

In [0]:
top_3_diesel_pd = top_3_diesel.toPandas()
bottom_3_diesel_pd = bottom_3_diesel.toPandas()

# Plot the results using Plotly

fig_top = px.bar(top_3_diesel_pd,
                  x='district', 
                  y='avg(sales_growth_diesel)', 
                  title='Top 3 Districts - Diesel Sales Growth',
                  text=top_3_diesel_pd['avg(sales_growth_diesel)']
)

fig_top.update_layout(
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
)

fig_bottom = px.bar(bottom_3_diesel_pd, 
                    x='district', 
                    y='avg(sales_growth_diesel)',
                    
                    title='Bottom 3 Districts - Diesel Sales Growth',
                    text=bottom_3_diesel_pd['avg(sales_growth_diesel)']
)

fig_bottom.update_traces(marker_color='red')

fig_bottom.update_layout(
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
)

# Display the plots
fig_top.show()
fig_bottom.show()

In [0]:
# Display the results for electric fuel type
print("Top 3 District with Highest Electric Sales Growth:")
display(top_3_electric)

print("Bottom 3 District with Lowest Electric Sales Growth:")
display(bottom_3_electric)

Top 3 District with Highest Electric Sales Growth:


district avg(sales_growth_electric) Siddipet 185.02161982083024 Adilabad 120.70459496930089 Nizamabad 118.15453373111508

Bottom 3 District with Lowest Electric Sales Growth:


district avg(sales_growth_electric) Nagarkurnool 8.111907156024804 Mahabubabad 0.0 Kumurambheem Asifabad -11.111111111111109

In [0]:
top_3_electric_pd = top_3_electric.toPandas()
bottom_3_electric_pd = bottom_3_electric.toPandas()

# Plot the results using Plotly

fig_top = px.bar(top_3_electric_pd,
                  x='district', 
                  y='avg(sales_growth_electric)', 
                  title='Top 3 Districts - Electric Sales Growth',
                  text=top_3_electric_pd['avg(sales_growth_electric)']
)

fig_top.update_layout(
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
)

fig_bottom = px.bar(bottom_3_electric_pd, 
                    x='district', 
                    y='avg(sales_growth_electric)',
                    
                    title='Bottom 3 Districts - Electric Sales Growth',
                    text=bottom_3_electric_pd['avg(sales_growth_electric)']
)

fig_bottom.update_traces(marker_color='red')

fig_bottom.update_layout(
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid  
    plot_bgcolor='black',
)

# Display the plots
fig_top.show()
fig_bottom.show()

# <=Telangana State Industrial Project Approval and Self Certification System=>

## _TS-IPASS Problem Statement 8 =>_

### List down the top 5 sectors that have witnessed the most significant investments in FY 2022.


In [0]:
# Select relevant columns
relevant_columns = ['dist_code', 'month', 'sector', 'investment in cr']
sector_data = df5.select(relevant_columns).join(df2['month','fiscal_year'],'month')\
    .filter(col('fiscal_year')==2022)\
    .drop('month','dist_code')
# Filter data for FY 2022
display(sector_data)

sector investment in cr fiscal_year Engineering 38.2726 2022 Agro based incl Cold Storages 0.24 2022 Beverages 0.075 2022 Agro based incl Cold Storages 0.08 2022 Food Processing 1.5573 2022 Food Processing 0.24 2022 Cement, Cement & Concrete Products, Fly Ash Bricks 0.105 2022 Food Processing 0.957 2022 Others 3.7661 2022 Granite and Stone Crushing 4.861 2022 Food Processing 0.6166 2022 Paper and Printing 9.9579 2022 Granite and Stone Crushing 3.2 2022 Food Processing 0.17 2022 Paper and Printing 6.3 2022 Others 32.3953 2022 Plastic and Rubber 26.4618 2022 Granite and Stone Crushing 2.69 2022 Engineering 0.095 2022 Granite and Stone Crushing 0.986 2022 Wood and Leather 0.147 2022 Food Processing 2.7111 2022 Engineering 0.1767 2022 Cement, Cement & Concrete Products, Fly Ash Bricks 0.7608 2022 Beverages 0.1 2022 Pharmaceuticals and Chemicals 4.5011 2022 Beverages 0.24 2022 Electrical and Electronic Products 8.149 2022 Plastic and Rubber 0.245 2022 Electrical and Electronic Products 1.078 2022 Cement, Cement & Concrete Products, Fly Ash Bricks 0.16 2022 Pharmaceuticals and Chemicals 7.5 2022 Agro based incl Cold Storages 1.1053 2022 Cement, Cement & Concrete Products, Fly Ash Bricks 0.49 2022 Engineering 0.4116 2022 Food Processing 0.75 2022 Engineering 0.065 2022 Fertlizers Organic and Inorganic,Pesticides,Insecticides, and Other Related 1.5 2022 Food Processing 2.13 2022 Granite and Stone Crushing 4.42 2022 Others 8.3883 2022 Plastic and Rubber 0.2 2022 Beverages 0.4 2022 Engineering 0.309 2022 Food Processing 4.7 2022 Paper and Printing 0.22 2022 Pharmaceuticals and Chemicals 0.5229 2022 Plastic and Rubber 2.638 2022 Food Processing 0.1592 2022 Others 0.93 2022 Food Processing 3.9054 2022 Fertlizers Organic and Inorganic,Pesticides,Insecticides, and Other Related 0.97 2022 Engineering 2.4506 2022 Pharmaceuticals and Chemicals 0.1 2022 Granite and Stone Crushing 8.25 2022 Others 0.95 2022 Food Processing 0.16 2022 Others 0.24 2022 Textiles 0.1 2022 Food Processing 3.3462 2022 Engineering 0.23 2022 Textiles 1.11 2022 Food Processing 4.3 2022 Others 1.1 2022 Pharmaceuticals and Chemicals 102.63 2022 Agro based incl Cold Storages 0.65 2022 Cement, Cement & Concrete Products, Fly Ash Bricks 1.0596 2022 Engineering 0.11 2022 Fertlizers Organic and Inorganic,Pesticides,Insecticides, and Other Related 0.1 2022 Food Processing 0.4175 2022 Granite and Stone Crushing 1.453 2022 Automobile 2.0 2022 Cement, Cement & Concrete Products, Fly Ash Bricks 0.625 2022 Cement, Cement & Concrete Products, Fly Ash Bricks 0.145 2022 Food Processing 0.6799 2022 Agro based incl Cold Storages 0.1 2022 Engineering 0.022 2022 Solar and Other Renewable Energy 74.79 2022 Granite and Stone Crushing 0.2 2022 Beverages 5.75 2022 Granite and Stone Crushing 0.115 2022 Solar and Other Renewable Energy 190.182 2022 Pharmaceuticals and Chemicals 22.0 2022 Pharmaceuticals and Chemicals 2.36 2022 Pharmaceuticals and Chemicals 35.0 2022 R&D 432.4276 2022 Pharmaceuticals and Chemicals 0.12 2022 Plastic and Rubber 1.235 2022 Engineering 0.03 2022 Plastic and Rubber 8.42 2022 Pharmaceuticals and Chemicals 51.9892 2022 Paper and Printing 1.52 2022 Others 1.22 2022 Granite and Stone Crushing 2.4996 2022 Engineering 13.728 2022 Engineering 0.13 2022 Electrical and Electronic Products 0.6889 2022 Agro based incl Cold Storages 1.0 2022 Others 47.0 2022 Food Processing 6.0 2022 Beverages 0.07 2022 Cement, Cement & Concrete Products, Fly Ash Bricks 0.051 2022 Food Processing 24.252 2022 Others 0.08 2022 Textiles 2.0579 2022 Agro based incl Cold Storages 26.855 2022 Others 0.22 2022 Wood and Leather 1.0 2022 Cement, Cement & Concrete Products, Fly Ash Bricks 0.8 2022 Solar and Other Renewable Energy 0.44 2022 Food Processing 0.5 2022 Beverages 0.5 2022 Others 2.4 2022 Food Processing 2.63 2022 Engineering 0.06 2022 Agro based incl Cold Storages 0.9 2022 Food Processing 0.76 2022 Engineering 4.3199 2022 Others 6.6275 2022 Paper and Printing 5.8058 2022 Pharmaceuticals and Chemica

In [0]:
# Group by sector and sum the investments
sector_investments = sector_data.groupBy('sector').agg(F.sum('investment in cr').alias('total_investment'))

# Rank sectors based on total investment
window_spec = Window.orderBy(F.desc('total_investment'))
ranked_sectors = sector_investments.withColumn('rank', F.rank().over(window_spec))

# Select the top 5 sectors
top_5_sectors = ranked_sectors.filter('rank <= 5').select('sector', 'total_investment')

# Display the result
print("Top 5 Sectors with the Most Significant Investments in FY 2022:")
display(top_5_sectors)

Top 5 Sectors with the Most Significant Investments in FY 2022:


sector total_investment Plastic and Rubber 5855.609500000001 Pharmaceuticals and Chemicals 2181.634200000001 Real Estate,Industrial Parks and IT Buildings 2127.2963 Solar and Other Renewable Energy 2052.985 Engineering 1877.4533000000004

In [0]:
top_5_sectors_pd = top_5_sectors.toPandas()
top_5_sectors_pd

sector  total_investment
0                             Plastic and Rubber         5855.6095
1                  Pharmaceuticals and Chemicals         2181.6342
2  Real Estate,Industrial Parks and IT Buildings         2127.2963
3               Solar and Other Renewable Energy         2052.9850
4                                    Engineering         1877.4533

In [0]:
# Create a bar chart using Plotly
fig = px.bar(top_5_sectors_pd, x='sector', y='total_investment',
             labels={'total_investment': 'Total Investment (in crore)', 'sector': 'Sectors'},
             color='sector',  # Color by sector for better differentiation
             color_discrete_sequence=px.colors.qualitative.Set1,
             text = top_5_sectors_pd['total_investment'],
             
 )

# Customize layout if needed
fig.update_layout(
    title='Top 5 Sectors with Highest Investments in FY 2022',
    
    xaxis_title='Sectors',
    yaxis_title='Total Investment (in crore)',
    bargap=0.2,
    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid
    plot_bgcolor='black',  # Background color
)

fig.show()

In [0]:
# Create a pie chart using Plotly
fig = px.pie(top_5_sectors_pd, values='total_investment', names='sector',
             title='Top 5 Sectors with Highest Investments in FY 2022',
             labels={'total_investment': 'Total Investment (in crore)', 'sector': 'Sectors'},
             color='sector',  # Color by sector for better differentiation
             color_discrete_sequence=px.colors.qualitative.Set1,
             )

# Customize layout if needed
fig.update_layout(
    plot_bgcolor='black',  # Background color
)

fig.show()

## _TS-IPASS Problem Statement 9 =>_

### List down the top 3 districts that have attracted the most significant sector investments during FY 2019 to 2022? What factors could have led to the substantial investments in these particular districts?


In [0]:
# Select relevant columns
relevant_columns = ['dist_code', 'month', 'sector', 'investment in cr']

# Join df5 with df2 on the 'month' column
sector_data = df5.select(relevant_columns).join(df2['month', 'fiscal_year'], 'month').filter((F.col('fiscal_year') >= 2019) & (F.col('fiscal_year') <= 2022)).drop('month')
sector_data = sector_data.join(df1,'dist_code').drop('fiscal_year')

# Calculate total sector investment for each district and retrieve the district with the highest investment
district_code_sector_investment = sector_data.groupBy('district','sector') \
    .agg(
        F.sum('investment in cr').alias('total_investment'),
        F.first('district').alias('top_districts')

    ) \
    .orderBy(F.desc('total_investment'))

# display(district_code_sector_investment)

# Define a window specification for ranking districts within each sector
district_window = Window.orderBy(F.desc('total_investment'))

# Rank districts based on total investment across all sectors
district_sector_investment = district_code_sector_investment.withColumn('rank', F.dense_rank().over(district_window)).filter(col('rank')<=3)
display(district_sector_investment)

# district_sector_investment = district_code_sector_investment.join(df1,'dist_code').drop('dist_code')
# district_sector_investment = district_sector_investment.orderBy(F.desc('total_investment'))
# display(district_sector_investment)


district sector total_investment top_districts rank Rangareddy Real Estate,Industrial Parks and IT Buildings 28970.272899999996 Rangareddy 1 Peddapalli Fertlizers Organic and Inorganic,Pesticides,Insecticides, and Other Related 5254.28 Peddapalli 2 Rangareddy Plastic and Rubber 4993.3884 Rangareddy 3

## TS-IPASS Problem Statement 10=>

### Is there any relationship between district investments, vehicles sales and stamps revenue within the same district between FY 2021 and 2022?

In [0]:
# Select relevant columns from each dataframe
df2_selected = df2.select("month", "fiscal_year")

df3_selected = df3.select('dist_code', 'month', 'documents_registered_rev')

df4_selected = df4.select("dist_code", "month",
                          "vehicleClass_MotorCycle", "vehicleClass_MotorCar", "vehicleClass_AutoRickshaw","vehicleClass_Agriculture")

df5_selected = df5.select("dist_code", "month", "investment in cr")

# Join dataframes on common columns
merged = df3_selected.join(df4_selected, on=["dist_code", "month"], how="inner")\
    .join(df5_selected, on=["dist_code", "month"], how="inner")

# Calculate the total vehicle sales for each district
total_vehicle_sales = merged.withColumn(
    "total_vehicle_sales",
    F.col("vehicleClass_MotorCycle") +
    F.col("vehicleClass_MotorCar") +
    F.col("vehicleClass_AutoRickshaw") +
    F.col("vehicleClass_Agriculture")
)

# Select relevant columns and drop the unnecessary ones
merged_df = total_vehicle_sales.join(df2_selected, 'month', 'inner')\
    .filter((col('fiscal_year') >= 2021) & (col('fiscal_year') <= 2022))\
    .drop('month', 'fiscal_year','vehicleClass_MotorCycle', 'vehicleClass_MotorCar', 'vehicleClass_AutoRickshaw', 'vehicleClass_Agriculture')

merged_df = merged_df.groupBy('dist_code')\
    .agg(

        F.sum('documents_registered_rev').alias('total_stamps_rev'),
        F.sum('total_vehicle_sales').alias('total_vehicle_sales'),
        F.sum('investment in cr').alias('total_investment'),

)

display(merged_df)    


dist_code total_stamps_rev total_vehicle_sales total_investment 20_3 2163036958 78976 76.69969999999998 14_1 8490217751 222152 2260.6730000000007 20_2 4250758974 193394 80.64649999999999 15_1 626019418637 3825498 12406.300999999994 19_3 2711139754 94183 187.34300000000002 19_4 182144043 21691 17.0228 23_1 10499590064 339604 1510.8807 17_2 148362255759 1181937 8314.276 19_2 1346596092 80731 40.552299999999995 21_5 2424643964 123108 105.71790000000001 20_4 3347323510 98102 93.236 17_3 7217813287 218094 1504.0514999999998 23_3 28166661677 319196 1710.0968000000012 21_2 1531758175 265438 115.89810000000001 18_1 10114813222 341748 123.39270000000008 22_1 20512490190 456504 320.1977 23_2 3943512571 119863 1343.0537000000006 15_2 475712196345 4849695 4950.939199999997 16_1 14361064404 318133 35.629999999999995 17_1 5788991826 187253 2070.5875 14_2 698999465 34985 109.00900000000001 18_2 2194657133 123040 971.5848 15_3 3240741193 265397 205.6915 14_4 892963946 27548 400.5114 19_1 1292739277 55874 9.477999999999998 20_1 15883657814 337775 217.9012999999999 21_3 2115563407 76394 119.08079999999997 22_2 1550086157 152568 1021.0969999999999 14_3 2080568671 88455 284.60069999999996

In [0]:
# Select relevant numeric columns
numeric_columns = ["total_vehicle_sales", "total_stamps_rev", "total_investment"]

# Create a vector assembler to combine numeric columns into a single vector column
assembler = VectorAssembler(inputCols=numeric_columns, outputCol="features")
assembled_df = assembler.transform(merged_df)

# Compute the correlation matrix
correlation_matrix = Correlation.corr(assembled_df, "features").collect()[0][0]

# Convert correlation matrix to a Pandas DataFrame for plotting
correlation_df = pd.DataFrame(correlation_matrix.toArray(), columns=numeric_columns, index=numeric_columns)

# Round the values in the DataFrame to three decimal places
correlation_df_rounded = correlation_df.round(3)

# Create a heatmap using Plotly
fig = ff.create_annotated_heatmap(z=correlation_df_rounded.values,
                                  x=list(correlation_df_rounded.columns),
                                  y=list(correlation_df_rounded.index),
                                  zmin=correlation_df_rounded.min().min(),  # Set the minimum value
                                  zmax=correlation_df_rounded.max().max(),  # Set the maximum value
                                  colorscale="Viridis")

fig.update_layout(
    title="Correlation Matrix",
    xaxis_title="Variables",
    yaxis_title="Variables"
)

# Show the interactive plot
fig.show()

In [0]:
district_merged_df = merged_df.join(df1,'dist_code','inner').drop('dist_code')
display(district_merged_df)

total_stamps_rev total_vehicle_sales total_investment district 2163036958 78976 76.69969999999998 Rajanna Sircilla 8490217751 222152 2260.6730000000007 Mahabubnagar 4250758974 193394 80.64649999999999 Jagtial 626019418637 3825498 12406.300999999994 Rangareddy 2711139754 94183 187.34300000000002 Mancherial 182144043 21691 17.0228 Kumurambheem Asifabad 10499590064 339604 1510.8807 Nalgonda 148362255759 1181937 8314.276 Sangareddy 1346596092 80731 40.552299999999995 Nirmal 2424643964 123108 105.71790000000001 Mahabubabad 3347323510 98102 93.236 Peddapalli 7217813287 218094 1504.0514999999998 Siddipet 28166661677 319196 1710.0968000000012 Yadadri Bhuvanagiri 1531758175 265438 115.89810000000001 Warangal 10114813222 341748 123.39270000000008 Nizamabad 20512490190 456504 320.1977 Khammam 3943512571 119863 1343.0537000000006 Suryapet 475712196345 4849695 4950.939199999997 Medchal_Malkajgiri 14361064404 318133 35.629999999999995 Hyderabad 5788991826 187253 2070.5875 Medak 698999465 34985 109.00900000000001 Jogulamba Gadwal 2194657133 123040 971.5848 Kamareddy 3240741193 265397 205.6915 Vikarabad 892963946 27548 400.5114 Wanaparthy 1292739277 55874 9.477999999999998 Adilabad 15883657814 337775 217.9012999999999 Karimnagar 2115563407 76394 119.08079999999997 Jangoan 1550086157 152568 1021.0969999999999 Bhadradri Kothagudem 2080568671 88455 284.60069999999996 Nagarkurnool

In [0]:
district_merged_df_pd = district_merged_df.toPandas()

# Create a bar chart for investment in cr
fig1 = px.bar(district_merged_df_pd, 
              x='district', 
              y='total_investment', 
              color='district',
              text = district_merged_df_pd['total_investment'],
              title='Investment in CR Across Districts')

             
 

# Customize layout if needed
fig1.update_layout(

    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid
    plot_bgcolor='black',  # Background color

)

# Create a bar chart for total vehicle sales
fig2 = px.bar(district_merged_df_pd,
               x='district', 
               y='total_vehicle_sales', 
               color='district',
               text = district_merged_df_pd['total_vehicle_sales'],
               title='Total Vehicle Sales Across Districts')

# Customize layout if needed
fig2.update_layout(

    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid
    plot_bgcolor='black',  # Background color

)

# Create a bar chart for documents registered revenue
fig3 = px.bar(district_merged_df_pd,
               x='district', 
               y='total_stamps_rev', 
               color='district',
               text = district_merged_df_pd['total_stamps_rev'],
               title='Total Stamp Revenue Across Districts')

# Customize layout if needed
fig3.update_layout(

    xaxis=dict(showgrid=False),  # Disable x-axis grid
    yaxis=dict(showgrid=False),  # Disable y-axis grid
    plot_bgcolor='black',  # Background color

)

# Show the interactive plots
fig1.show()
fig2.show()
fig3.show()

# STOP SPARK SESSION

In [0]:
spark.stop()
print('SPARK SESSION TERMINATED SUCCESSFULLY')